In [2]:
import pandas as pd
import numpy as np
from pandas.tseries.offsets import *
import datetime
import os
import pickle
# day = '25'
# train = pd.read_csv("./data/train201710"+day+".csv", sep=",")
# train['O_TIME'] = pd.to_datetime('2017-10-'+day+' '+train['O_TIME'],format='%Y-%m-%d %H:%M:%S')
# train = train.groupby(['O_LINENO', 'O_TERMINALNO']).apply(lambda x:x.sort_values(by='O_TIME', ascending=True))

In [8]:
bus = train[(train['O_LINENO']==861)&(train['O_TERMINALNO']==905887)&(train['O_UP']==1)&(train['O_TIME']>'2017-10-25 06:00:00')&(train['O_TIME']<'2017-10-25 07:05:00')]
bus

O_LINENO  O_TERMINALNO              O_TIME  \
O_LINENO O_TERMINALNO                                                       
861      905887       4942901       861        905887 2017-10-25 06:45:49   
                      4942511       861        905887 2017-10-25 06:46:00   
                      4944421       861        905887 2017-10-25 06:46:10   
                      4943029       861        905887 2017-10-25 06:46:19   
                      4946074       861        905887 2017-10-25 06:46:29   
                      4948155       861        905887 2017-10-25 06:46:42   
                      4946943       861        905887 2017-10-25 06:46:52   
                      4945780       861        905887 2017-10-25 06:47:02   
                      4947863       861        905887 2017-10-25 06:47:12   
                      4947490       861        905887 2017-10-25 06:47:22   
                      4948580       861        905887 2017-10-25 06:47:32   
                      4950673       861        905887 2017-10-25 06:47:42   
                      4951557       861        905887 2017-10-25 06:47:52   
                      4950299       861        905887 2017-10-25 06:48:02   
                      4950137       861        905887 2017-10-25 06:48:12   
                      4948928       861        905887 2017-10-25 06:48:22   
                      4954446       861        905887 2017-10-25 06:48:32   
                      4953265       861        905887 2017-10-25 06:48:42   
                      4952071       861        905887 2017-10-25 06:48:52   
                      4954162       861        905887 2017-10-25 06:49:02   
                      4953188       861        905887 2017-10-25 06:49:12   
                      4951993       861        905887 2017-10-25 06:49:22   
                      4957368       861        905887 2017-10-25 06:49:32   
                      4956182       861        905887 2017-10-25 06:49:42   
                      4958269       861        905887 2017-10-25 06:49:52   
                      4955820       861        905887 2017-10-25 06:50:02   
                      4955660       861        905887 2017-10-25 06:50:12   
                      4957735       861        905887 2017-10-25 06:50:22   
                      4956337       861        905887 2017-10-25 06:50:32   
                      4958800       861        905887 2017-10-25 06:50:42   
                      4960881       861        905887 2017-10-25 06:50:52   
                      4959686       861        905887 2017-10-25 06:51:02   
                      4958707       861        905887 2017-10-25 06:51:12   
                      4960960       861        905887 2017-10-25 06:51:22   
                      4960612       861        905887 2017-10-25 06:51:32   
                      4961711       861        905887 2017-10-25 06:51:42   
                      4963805       861        905887 2017-10-25 06:51:52   
                      4961584       861        905887 2017-10-25 06:52:02   
                      4963637       861        905887 2017-10-25 06:52:12   
                      4963499       861        905887 2017-10-25 06:52:22   
                      4984963       861        905887 2017-10-25 06:59:12   
                      4987238       861        905887 2017-10-25 06:59:22   
                      4985835       861        905887 2017-10-25 06:59:32   
                      4987956       861        905887 2017-10-25 06:59:43   
                      4988769       861        905887 2017-10-25 06:59:52   

                               O_LONGITUDE  O_LATITUDE  O_SPEED  O_MIDDOOR  \
O_LINENO O_TERMINALNO                                                        
861      905887       4942901      117.132     39.1696        0          0   
                      4942511      117.132     39.1696        0          0   
                      4944421      117.132     39.1696        0          0   
                     

In [3]:
from math import sin, cos, sqrt, atan2, radians
def distance(coord1, coord2):
    R = 6373.0
    lat1 = radians(coord1[0])
    lon1 = radians(coord1[1])
    lat2 = radians(coord2[0])
    lon2 = radians(coord2[1])

    dlon = lon2 - lon1
    dlat = lat2 - lat1
    a = (sin(dlat/2))**2 + cos(lat1) * cos(lat2) * (sin(dlon/2))**2
    c = 2 * atan2(sqrt(a), sqrt(1-a))
    d = R * c
    return d

In [465]:
def get_station(bus1,line):
    # bus1[(bus1['O_SPEED'] == 0) & (bus1['O_LONGITUDE'] != 0.0) & (bus1['O_LATITUDE'] != 0.0)]
    leng = bus1.shape[0]
    d = 0
    for i in range(leng-1):
        start_bus = bus1.iloc[i]
        time = start_bus['O_TIME']
        station = start_bus['O_NEXTSTATIONNO']
        on = start_bus['O_UP']
        loc = [start_bus['O_LATITUDE'], start_bus['O_LONGITUDE']]
        
        if i == 0:
            start_t = time
            start_loc = loc
        
        next_bus = bus1.iloc[i+1]
        next_loc = [next_bus['O_LATITUDE'], next_bus['O_LONGITUDE']]
        next_time = next_bus['O_TIME']
        next_station = next_bus['O_NEXTSTATIONNO']
        
        if (next_station == station):
            d = d + distance(loc, next_loc)
                
        else:
            if (next_station > station):
                s = str(bus1['O_UP'].iloc[i+1])+','+str(next_station-1)+','+str(
                    bus1['O_LATITUDE'].iloc[i+1])+','+str(bus1['O_LONGITUDE'].iloc[i+1])+'\n'
                if (next_station == (station+1)):
                    d = d + distance(loc, next_loc)
                    diff_t = next_time - start_t
                    ss = str(bus1['O_UP'].iloc[i+1])+','+str(station-1)+','+str(
                        next_station-1)+','+str(d)+','+str(diff_t.seconds)+'\n'
                    with open('./'+day+'/'+str(line)+'-station.txt', 'a+') as fw2:
                        fw2.write(ss)
                    d = 0
                    start_t = next_time
            elif (next_station < station):
                s = str(bus1['O_UP'].iloc[i+1])+','+str(next_station-1)+','+str(
                    bus1['O_LATITUDE'].iloc[i])+','+str(bus1['O_LONGITUDE'].iloc[i])+'\n'
            with open('./'+day+'/'+str(line)+'-test.txt', 'a+') as fw:
                fw.write(s)
        #print(on,station,' to ',next_station,' diff time ',diff.seconds)

In [57]:
line = train['O_LINENO'].drop_duplicates()

day = '01'
bus1 = train[train['O_LINENO']==600]
get_station(bus1,600)
# import os
# if not os.path.exists('./'+day+'/'):
#     os.mkdir('./'+day+'/')
# line = train['O_LINENO'].drop_duplicates()
# print(line.shape)
# for i in range(line.shape[0]):
#     l = line.iloc[i]
#     buses = train[train['O_LINENO']==l]
# #     print(l, buses.shape)
#     get_station(buses,l)
# print("finished")

In [42]:
day='01'
path = './'+day+'/'+str(652)+'-station.txt';
bus = pd.read_table(path,header=None,sep=',',encoding='utf-8')
bus.columns=['O_UP',"From","To","Distance",'O_TIME']


In [55]:
bus0 = bus[(bus['O_UP']==0)&(bus['From']==1)&(bus['To']==2)]#.groupby(['O_LATITUDE','O_LONGITUDE'])['O_UP'].count().reset_index()
bus0 = bus0[(bus0['Distance']<50)&(bus0['O_TIME']<1500)]
bus0.sort_values(by='Distance', ascending=False)
# bus0['Distance'].mean()
# bus.groupby(['O_UP','From','To'])['Distance'].mean()#apply(lambda x:x.sort_values(by='Distance', ascending=False))#.mean()#['Distance']

O_UP  From  To  Distance  O_TIME
11435     0     1   2  4.344959     614
943       0     1   2  2.158521    1089
7998      0     1   2  1.759250     369
1295      0     1   2  1.707187     437
2433      0     1   2  1.699638     421
10153     0     1   2  1.684926     259
8370      0     1   2  1.665131     240
2297      0     1   2  1.647230    1178
6811      0     1   2  1.639130     250
8843      0     1   2  1.628007     369
10381     0     1   2  1.612877     291
13340     0     1   2  1.608041     439
4014      0     1   2  1.607672     320
8827      0     1   2  1.601990     316
1602      0     1   2  1.597338     337
9345      0     1   2  1.593119     345
3334      0     1   2  1.567312     954
7565      0     1   2  1.561325    1212
5637      0     1   2  1.551083     493
2882      0     1   2  1.528803    1137
359       0     1   2  1.527880     633
10645     0     1   2  1.525505     268
2718      0     1   2  1.522855     974
5806      0     1   2  1.512564     257
10900     0     1   2  1.498467    1410
12749     0     1   2  1.480339     306
9641      0     1   2  1.426054     850
4193      0     1   2  0.772971     401

In [59]:
import os
if not os.path.exists('./station/'):
    os.mkdir('./station/')
for i in range(line.shape[0]):
    num = line.iloc[i]
    bus = pd.DataFrame()
    station = pd.DataFrame()
    for d in range(1, 25):
        if d < 10:
            day = '0' + str(d)
        else:
            day = str(d)
            
        path = './'+str(day)+'/'+str(num)+'.txt';
        if os.path.exists(path):
            busx = pd.read_table(path,header=None,sep=' ',encoding='utf-8')
            bus = pd.concat([bus,busx])
        path = './'+str(day)+'/'+str(num)+'-station.txt';
        if os.path.exists(path):
            stationx = pd.read_table(path,header=None,sep=',',encoding='utf-8')
            station = pd.concat([station,stationx])
    
    #all days  
    bus.columns=["O_UP","Station","O_LATITUDE","O_LONGITUDE"]
    bus = bus[(bus['O_LONGITUDE'] != 0.0) & (bus['O_LATITUDE'] != 0.0)]

    station.columns=['O_UP',"From","To","Distance",'O_TIME']
    station = station[(station['Distance']<50)&(station['O_TIME']<1800)]

    # bus
    stations = bus['Station'].drop_duplicates()
    for up in range(2):
        for s in range(1,stations.shape[0]+1): 
            station0 = station[(station['O_UP']==up)&(station['From']==s)&(station['To']==(s+1))]
            station0 = station0.sort_values(by='Distance', ascending=False)
            d = station0['Distance'].mean()
            s = str(up)+','+str(s)+','+str(s+1)+','+str(d)
            with open('./station/'+str(num)+'-test.txt','a+') as fw:            #with方式不需要再进行close
                fw.write(s+'\n')
print("station finished")

station finished


In [158]:
if not os.path.exists('./station/'):
    os.mkdir('./station/')
for i in range(line.shape[0]):
    num = line.iloc[i]
    bus = pd.DataFrame()
    for d in range(1, 25):
        if d < 10:
            day = '0' + str(d)
        else:
            day = str(d)
        path = './'+str(day)+'/'+str(num)+'.txt';
        if os.path.exists(path):
            busx = pd.read_table(path,header=None,sep=' ',encoding='utf-8')
            bus = pd.concat([bus,busx])
    #all days        
    bus.columns=["O_UP","Station","O_LATITUDE","O_LONGITUDE"]
    bus = bus[(bus['O_LONGITUDE'] != 0.0) & (bus['O_LATITUDE'] != 0.0)]
    # bus
    stations = bus['Station'].drop_duplicates()
    for up in range(2):
        for s in range(1,stations.shape[0]+1): 
            bus0 = bus[(bus['O_UP']==up)&(bus['Station']==s)].groupby(['O_LATITUDE','O_LONGITUDE'])['O_UP'].count().reset_index()
            bus0 = bus0.sort_values(by='O_UP', ascending=False)
            s = str(up)+' , '+str(s)+' , '+str(bus0[:5].mean()['O_LATITUDE'])+' , '+str(bus0[:5].mean()['O_LONGITUDE'])
            with open('./station/+str(num)'+'.txt','a+') as fw:            #with方式不需要再进行close
                fw.write(s+'\n')
print("station finished")

O_LATITUDE  O_LONGITUDE  O_UP
6      39.1746      117.164     8
13     39.1751      117.163     7
2      39.1744      117.164     4
4      39.1745      117.164     4
0       0.0000        0.000     2
7      39.1747      117.163     2
9      39.1748      117.164     2
12     39.1750      117.163     2
1      39.1743      117.164     1
3      39.1745      117.163     1
5      39.1746      117.163     1
8      39.1748      117.163     1
10     39.1749      117.163     1
11     39.1749      117.164     1

In [273]:
day = '01'
bus1 = train[train['O_LINENO']==652]
get_station(bus1,652)

In [464]:
bus1 = bus1[(bus1['O_LONGITUDE'] != 0) & (bus1['O_LATITUDE'] != 0)]
leng = bus1.shape[0]
time = 0
target = 2
for i in range(leng-1):
    station = bus1['O_NEXTSTATIONNO'].iloc[i]

    next_time = bus1['O_TIME'].iloc[i+1] #t1
    next_station = bus1['O_NEXTSTATIONNO'].iloc[i+1]
    if (station != target and target == next_station):

        Pend = next_time + Second(20)
        Pstart = next_time - Second(20)
        Pdata = bus1[(bus1['O_TIME']>=Pstart) & (bus1['O_TIME']<=Pend) & (bus1['O_SPEED']==0)]
        if (Pdata.shape[0] > 0):
            t = Pdata['O_TIME'].iloc[0]
        else:
            t = next_time
        print(t)
#         if(Pdata.shape[0]>0):
#             s = str(bus1['O_UP'].iloc[i+1])+' '+str(next_station-1)+' '+str(Pdata['O_LATITUDE'].iloc[0])+' '+str(Pdata['O_LONGITUDE'].iloc[0])+'\n'
#         else:
#             s = str(bus1['O_UP'].iloc[i+1])+' '+str(next_station-1)+' '+str(bus1['O_LATITUDE'].iloc[i+1])+' '+str(bus1['O_LONGITUDE'].iloc[i+1])+'\n'


2017-10-01 06:00:03
2017-10-01 09:17:36
2017-10-01 12:43:51
2017-10-01 19:31:09
2017-10-01 09:03:46
2017-10-01 12:35:43
2017-10-01 15:49:10
2017-10-01 06:00:03
2017-10-01 09:34:42
2017-10-01 16:13:10
2017-10-01 18:57:38
2017-10-01 07:48:14
2017-10-01 07:49:23
2017-10-01 11:18:28
2017-10-01 18:38:58
2017-10-01 21:11:39
2017-10-01 06:19:17
2017-10-01 10:06:22
2017-10-01 16:31:30
2017-10-01 08:35:24
2017-10-01 18:34:51
2017-10-01 06:39:27
2017-10-01 10:11:22
2017-10-01 17:08:24
2017-10-01 20:04:45
2017-10-01 06:55:43
2017-10-01 10:18:51
2017-10-01 17:22:00
2017-10-01 06:21:37
2017-10-01 09:53:21
2017-10-01 16:50:00
2017-10-01 07:29:44
2017-10-01 11:01:51
2017-10-01 14:30:20
2017-10-01 18:09:31
2017-10-01 20:53:23
2017-10-01 07:26:04
2017-10-01 07:37:18
2017-10-01 11:13:45
2017-10-01 14:39:58
2017-10-01 17:51:45
2017-10-01 20:24:25
2017-10-01 06:58:52
2017-10-01 07:06:13
2017-10-01 10:27:42
2017-10-01 17:30:51
2017-10-01 20:19:04
2017-10-01 10:49:32
2017-10-01 14:18:27
2017-10-01 18:21:51


In [231]:
if not os.path.exists('./station/'):
    os.mkdir('./station/')
num = 600
bus = pd.DataFrame()
for d in range(1, 25):
    if d < 10:
        day = '0' + str(d)
    else:
        day = d
    path = './'+str(day)+'/'+str(num)+'.txt';
    if os.path.exists(path):
        busx = pd.read_table(path,header=None,sep=' ',encoding='utf-8')
        bus = pd.concat([bus,busx])
#all days        
bus.columns=["O_UP","Station","O_LATITUDE","O_LONGITUDE"]
bus = bus[(bus['O_LONGITUDE'] != 0.0) & (bus['O_LATITUDE'] != 0.0)]
# bus
stations = bus['Station'].drop_duplicates()
for up in range(2):
    for s in range(1,stations.shape[0]+1): 
        bus0 = bus[(bus['O_UP']==up)&(bus['Station']==s)].groupby(['O_LATITUDE','O_LONGITUDE'])['O_UP'].count().reset_index()
        bus0 = bus0.sort_values(by='O_UP', ascending=False)
        s = str(up)+' , '+str(s)+' , '+str(bus0[:5].mean()['O_LATITUDE'])+' , '+str(bus0[:5].mean()['O_LONGITUDE'])
        with open('./station/'+str(num)+'.txt','a+') as fw:            #with方式不需要再进行close
            fw.write(s+'\n')
print(day, "station finished")

(2064, 4)
(4212, 4)
(6354, 4)
(8483, 4)
(10473, 4)
(12576, 4)
(12576, 4)
(12576, 4)
(12576, 4)
(12576, 4)
(12576, 4)
(12576, 4)
(12576, 4)
(12576, 4)
(12576, 4)
(12576, 4)
(12576, 4)
(12576, 4)
(12576, 4)
(12576, 4)
(12576, 4)
(12576, 4)
(12576, 4)
(12576, 4)


In [5]:
def get_last_station(bus1):
    # bus1[(bus1['O_SPEED'] == 0) & (bus1['O_LONGITUDE'] != 0.0) & (bus1['O_LATITUDE'] != 0.0)]
    len = bus1.shape[0]
    d = 0
    for i in range(len-1,0,-1):
        start_bus = bus1.iloc[i-1]
        station = start_bus['O_NEXTSTATIONNO']
        loc = [start_bus['O_LATITUDE'], start_bus['O_LONGITUDE']]

        next_bus = bus1.iloc[i]
        next_station = next_bus['O_NEXTSTATIONNO']
        next_loc = [next_bus['O_LATITUDE'], next_bus['O_LONGITUDE']]

        if (next_station == station):
            d = d + distance(loc, next_loc)
        if (next_station > station):
            return next_station-1,bus1.iloc[i]['O_UP'],bus1.iloc[i],d
        elif (next_station < station):
            return next_station-1,bus1.iloc[i]['O_UP'],bus1.iloc[i-1],d

In [262]:
bus1 = train[train['O_TERMINALNO']==903015]
bus1 = bus1[(bus1['O_TIME']<'2017-10-27 19:00:00') & (bus1['O_TIME']>'2017-10-27 18:00:00')]
bus1[bus1['O_SPEED']>0]

Empty DataFrame
Columns: [O_LINENO, O_TERMINALNO, O_TIME, O_LONGITUDE, O_LATITUDE, O_SPEED, O_MIDDOOR, O_REARDOOR, O_FRONTDOOR, O_UP, O_RUN, O_NEXTSTATIONNO]
Index: []

In [90]:
get_last_station(bus1)


(10, O_LINENO                           711
 O_TERMINALNO                    906948
 O_TIME             2017-10-27 12:59:33
 O_LONGITUDE                    117.204
 O_LATITUDE                     39.0093
 O_SPEED                             11
 O_MIDDOOR                            0
 O_REARDOOR                           0
 O_FRONTDOOR                          0
 O_UP                                 0
 O_RUN                                1
 O_NEXTSTATIONNO                     11
 Name: (711, 906948, 7352120), dtype: object)

In [263]:
#get all routes
bus = pd.DataFrame()
for i in range(line.shape[0]):
    num = line.iloc[i]

    path = './station/'+str(num)+'.txt';
    if os.path.exists(path):
        bus1 = pd.read_table(path,header=None,sep=',',encoding='utf-8')
        bus1.columns=["O_UP","Station","O_LATITUDE","O_LONGITUDE"]  
        bus1['O_LINENO'] = num
        bus = pd.concat([bus,bus1])
bus.groupby(['O_LINENO','O_UP']).apply(lambda x:x.sort_values(by='Station', ascending=True))

O_UP  Station            O_LATITUDE          O_LONGITUDE  \
O_LINENO O_UP                                                                 
600      0    0       0        1              39.1747              117.1636   
              1       0        2   39.147079999999995               117.174   
              2       0        3             39.14524    117.16780000000001   
              3       0        4   39.144619999999996               117.165   
              4       0        5   39.138920000000006               117.165   
              5       0        6   39.132400000000004               117.167   
              6       0        7              39.1288               117.168   
              7       0        8               39.125               117.168   
              8       0        9    39.12179999999999                117.17   
              9       0       10             39.11992    117.17559999999999   
              10      0       11   39.119099999999996    117.18199999999999   
              11      0       12   39.118579999999994              117.1874   
              12      0       13    39.11674000000001    117.19539999999999   
              13      0       14             39.11555               117.203   
              14      0       15   39.117239999999995    117.21079999999999   
              15      0       16                39.12              117.2172   
              16      0       17              39.1292    117.22200000000001   
              17      0       18              39.1369    117.21399999999998   
              18      0       19              39.1412                117.21   
              19      0       20   39.144079999999995               117.208   
              20      0       21              39.1491              117.2018   
              21      0       22              39.1476    117.19800000000001   
              22      0       23              39.1465    117.19000000000001   
              23      0       24             39.14492              117.1824   
              24      0       25    39.14507999999999              117.1774   
              25      0       26             39.14606               117.175   
         1    26      1        1             39.17466              117.1636   
              27      1        2             39.14528              117.1762   
              28      1        3    39.14486000000001    117.17839999999998   
              29      1        4             39.14538              117.1848   
...                 ...      ...                   ...                  ...   
652      1    138     1       55               38.9118              117.425   
              139     1       56               38.9063              117.429   
              140     1       57               38.8991              117.435   
              141     1       58               38.8946              117.438   
              142     1       59               38.8885              117.444   
              143     1       60               38.8842              117.451   
              144     1       61               38.8743              117.457   
              145     1       62               38.8677              117.461   
              146     1       63               38.8589              117.465   
              147     1       64               38.8544              117.466   
              148     1       65               38.8501              117.469   
              149     1       66               38.8444               117.47   
              150     1       67               38.8441              117.464   
              151     1       68               38.8435              117.453   
              152     1       69               38.8432               117.45   
              153     1       70               38.8408              117.444   
              154     1       71               38.8371              117.444   
              155     1       72               38.8311              1

In [107]:
train[train['O_LINENO']==652]

O_LINENO  O_TERMINALNO              O_TIME  \
O_LINENO O_TERMINALNO                                                       
652      900424       3575033       652        900424 2017-10-27 10:00:06   
                      3574684       652        900424 2017-10-27 10:00:16   
                      3574031       652        900424 2017-10-27 10:00:26   
                      3573689       652        900424 2017-10-27 10:00:36   
                      3578693       652        900424 2017-10-27 10:00:46   
                      3578346       652        900424 2017-10-27 10:00:56   
                      3577337       652        900424 2017-10-27 10:01:05   
                      3614644       652        900424 2017-10-27 10:01:15   
                      3613037       652        900424 2017-10-27 10:01:25   
                      3610599       652        900424 2017-10-27 10:01:35   
                      3609776       652        900424 2017-10-27 10:01:45   
                      3608181       652        900424 2017-10-27 10:01:55   
                      3607344       652        900424 2017-10-27 10:02:05   
                      3605738       652        900424 2017-10-27 10:02:15   
                      3617508       652        900424 2017-10-27 10:02:25   
                      3615884       652        900424 2017-10-27 10:02:35   
                      3614273       652        900424 2017-10-27 10:02:45   
                      3613444       652        900424 2017-10-27 10:02:55   
                      3611834       652        900424 2017-10-27 10:03:05   
                      3610193       652        900424 2017-10-27 10:03:15   
                      3608558       652        900424 2017-10-27 10:03:25   
                      3606136       652        900424 2017-10-27 10:03:35   
                      3618703       652        900424 2017-10-27 10:03:45   
                      3617098       652        900424 2017-10-27 10:03:55   
                      3616289       652        900424 2017-10-27 10:04:05   
                      3628134       652        900424 2017-10-27 10:04:15   
                      3626522       652        900424 2017-10-27 10:04:25   
                      3624858       652        900424 2017-10-27 10:04:35   
                      3623218       652        900424 2017-10-27 10:04:45   
                      3621592       652        900424 2017-10-27 10:04:55   
...                                 ...           ...                 ...   
         903941       4926300       652        903941 2017-10-27 20:56:20   
                      4933071       652        903941 2017-10-27 20:56:30   
                      4926314       652        903941 2017-10-27 20:56:40   
                      4932287       652        903941 2017-10-27 20:56:50   
                      4934820       652        903941 2017-10-27 20:56:53   
                      4925536       652        903941 2017-10-27 20:56:59   
                      4928097       652        903941 2017-10-27 20:57:04   
                      4930621       652        903941 2017-10-27 20:57:08   
                      4932337       652        903941 2017-10-27 20:57:11   
                      4933180       652        903941 2017-10-27 20:57:12   
                      4923051       652        903941 2017-10-27 20:57:17   
                      4925570       652        903941 2017-10-27 20:57:21   
                      4965900       652        903941 2017-10-27 20:57:27   
                      4962467       652        903941 2017-10-27 20:57:37   
                      4965534       652        903941 2017-10-27 20:57:47   
                      4968427       652        903941 2017-10-27 20:57:57   
                      4964762       652        903941 2017-10-27 20:58:07   
                      4968059       652        903941 2017-10-27 20:58:17   
                      4964407       652        903941 2017-10-27 20:58:27   
                      49677

In [272]:
bus = train[(train['O_LINENO']==96)&(train['O_TERMINALNO']==907076)&(train['O_TIME']>'2017-10-29 09:00:00')&(train['O_TIME']<'2017-10-29 10:00:00')]
bus

O_LINENO  O_TERMINALNO              O_TIME  \
O_LINENO O_TERMINALNO                                                       
96       907076       8584272        96        907076 2017-10-29 09:00:01   
                      8584598        96        907076 2017-10-29 09:00:02   
                      8584618        96        907076 2017-10-29 09:00:03   
                      8587014        96        907076 2017-10-29 09:00:13   
                      8585787        96        907076 2017-10-29 09:00:25   
                      8583504        96        907076 2017-10-29 09:00:35   
                      8585799        96        907076 2017-10-29 09:00:45   
                      8583563        96        907076 2017-10-29 09:00:55   
                      8586124        96        907076 2017-10-29 09:01:05   
                      8586372        96        907076 2017-10-29 09:01:06   
                      8586418        96        907076 2017-10-29 09:01:07   
                      8584510        96        907076 2017-10-29 09:01:17   
                      8586729        96        907076 2017-10-29 09:01:27   
                      8584874        96        907076 2017-10-29 09:01:37   
                      8625098        96        907076 2017-10-29 09:01:47   
                      8619257        96        907076 2017-10-29 09:01:57   
                      8624279        96        907076 2017-10-29 09:02:04   
                      8625105        96        907076 2017-10-29 09:02:05   
                      8625951        96        907076 2017-10-29 09:02:06   
                      8626825        96        907076 2017-10-29 09:02:07   
                      8627622        96        907076 2017-10-29 09:02:08   
                      8627659        96        907076 2017-10-29 09:02:09   
                      8620985        96        907076 2017-10-29 09:02:19   
                      8615169        96        907076 2017-10-29 09:02:29   
                      8616001        96        907076 2017-10-29 09:02:30   
                      8616835        96        907076 2017-10-29 09:02:31   
                      8616861        96        907076 2017-10-29 09:02:32   
                      8617686        96        907076 2017-10-29 09:02:33   
                      8624411        96        907076 2017-10-29 09:02:43   
                      8616077        96        907076 2017-10-29 09:02:50   
...                                 ...           ...                 ...   
                      8699879        96        907076 2017-10-29 09:55:01   
                      8707420        96        907076 2017-10-29 09:55:11   
                      8699894        96        907076 2017-10-29 09:55:21   
                      8704981        96        907076 2017-10-29 09:55:31   
                      8698282        96        907076 2017-10-29 09:55:41   
                      8705042        96        907076 2017-10-29 09:55:51   
                      8699146        96        907076 2017-10-29 09:56:01   
                      8704232        96        907076 2017-10-29 09:56:11   
                      8698396        96        907076 2017-10-29 09:56:21   
                      8704306        96        907076 2017-10-29 09:56:31   
                      8697583        96        907076 2017-10-29 09:56:41   
                      8703510        96        907076 2017-10-29 09:56:51   
                      8697635        96        907076 2017-10-29 09:57:01   
                      8704401        96        907076 2017-10-29 09:57:11   
                      8697676        96        907076 2017-10-29 09:57:21   
                      8704429        96        907076 2017-10-29 09:57:31   
                      8699562        96        907076 2017-10-29 09:57:41   
                      8702031        96        907076 2017-10-29 09:57:51   
                      8703756        96        907076 2017-10-29 09:58:01   
                      87070

In [273]:
print(get_last_station(bus))


(1, 0, O_LINENO                            96
O_TERMINALNO                    907076
O_TIME             2017-10-29 09:34:01
O_LONGITUDE                    117.201
O_LATITUDE                     38.9818
O_SPEED                              9
O_MIDDOOR                            0
O_REARDOOR                           0
O_FRONTDOOR                          0
O_UP                                 1
O_RUN                                1
O_NEXTSTATIONNO                     45
Name: (96, 907076, 8650588), dtype: object)


In [23]:
def describe(x):
    if x=='多云':
        return 0
    elif x=='阴':
        return 1
    elif x=='晴':
        return 2
    elif x=='小雨':
        return 3
    else :
        return 4

def rain(d,n):
    if (int(d)>=3 or int(n)>=3):
        return 1
    else :
        return 0

weather = pd.read_csv("/home/b418-xiwei/xzl/notebook/DC/data/weather.txt", sep=",")
weather['days'] = pd.to_datetime(weather['days'],format='%Y年%m月%d日')
# weather[(weather['days']=='2017-10-'+str(train.iloc[1]['O_TIME'].day))]
# weather['dws'].drop_duplicates()
weather['dws_onehot'] = weather['dws'].apply(describe)
weather['nws_onehot'] = weather['nws'].apply(describe)
weather['is_rain'] = weather.apply(lambda x: rain(x['dws_onehot'], x['nws_onehot']), axis=1)
weather
# train.iloc[1]['O_TIME'].weekday()#0-4 workday

days dws nws  dts  nts    dwinds    nwinds  dws_onehot  nws_onehot  \
0  2017-10-01  多云  多云   25   16  东北风 4-5级  东北风 4-5级           0           0   
1  2017-10-02   阴   阴   21   12  东北风 3-4级   西北风 ≤3级           1           1   
2  2017-10-03  多云  多云   21   12    东风 ≤3级   西南风 ≤3级           0           0   
3  2017-10-04  多云   晴   22   13    南风 ≤3级   西南风 ≤3级           0           2   
4  2017-10-05  多云  多云   23   13  西南风 3-4级   西南风 ≤3级           0           0   
5  2017-10-06   晴  多云   25   15   西南风 ≤3级   西南风 ≤3级           2           0   
6  2017-10-07  小雨  小雨   19   14    南风 ≤3级   东北风 ≤3级           3           3   
7  2017-10-08  小雨  中雨   18   14   西北风 ≤3级  东北风 3-4级           3           4   
8  2017-10-09  中雨  中雨   16   10  东北风 4-5级  东北风 4-5级           4           4   
9  2017-10-10  小雨   阴   11    7   北风 3-4级    北风 ≤3级           3           1   
10 2017-10-11   晴  多云   16    8    北风 ≤3级    北风 ≤3级           2           0   
11 2017-10-12  多云  多云   17   10   西南风 ≤3级   东南风 ≤3级           0           0   
12 2017-10-13   晴   阴   19   11   西南风 ≤3级    东风 ≤3级           2           1   
13 2017-10-14  小雨  小雨   16   10   东风 3-4级    东风 ≤3级           3           3   
14 2017-10-15   阴  多云   18   11    西风 ≤3级    北风 ≤3级           1           0   
15 2017-10-16   晴  多云   19   11   东风 3-4级    东风 ≤3级           2           0   
16 2017-10-17   阴  小雨   17   10    东风 ≤3级    东风 ≤3级           1           3   
17 2017-10-18  小雨   阴   16   10    南风 ≤3级    南风 ≤3级           3           1   
18 2017-10-19  多云   晴   19   12   西北风 ≤3级   西南风 ≤3级           0           2   
19 2017-10-20   晴   晴   21   13   西南风 ≤3级   西南风 ≤3级           2           2   
20 2017-10-21   阴  小雨   19   10    东风 ≤3级  东北风 3-4级           1           3   
21 2017-10-22  多云  多云   16    8   东北风 ≤3级   东北风 ≤3级           0           0   
22 2017-10-23   晴   晴   17    7   西南风 ≤3级   西南风 ≤3级           2           2   
23 2017-10-24   晴  多云   18    9   西南风 ≤3级   西南风 ≤3级           2           0   
24 2017-10-25   阴   阴   17   10   西南风 ≤3级   西南风 ≤3级           1           1   
25 2017-10-26   阴   晴   19    9   西南风 ≤3级   西南风 ≤3级           1           2   
26 2017-10-27   晴   晴   21   12   西南风 ≤3级  西南风 3-4级           2           2   
27 2017-10-28  多云  多云   18    7   北风 5-6级   北风 5-6级           0           0   
28 2017-10-29   晴   晴   14    4  西北风 3-4级    西风 ≤3级           2           2   
29 2017-10-30   晴   晴   15    5   西南风 ≤3级   西南风 ≤3级           2           2   
30 2017-10-31  多云   晴   18    7   西南风 ≤3级   东北风 ≤3级           0           2   

    is_rain  
0         0  
1         0  
2         0  
3         0  
4         0  
5         0  
6         1  
7         1  
8         1  
9         1  
10        0  
11        0  
12        0  
13        1  
14        0  
15        0  
16        1  
17        1  
18        0  
19        0  
20        1  
21        0  
22        0  
23        0  
24        0  
25        0  
26        0  
27        0  
28        0  
29        0  
30        0

In [408]:
def get_feature(line,day):
#     feature = pd.DataFrame()
    # bus1[(bus1['O_SPEED'] == 0) & (bus1['O_LONGITUDE'] != 0.0) & (bus1['O_LATITUDE'] != 0.0)]
#     with open('./' + day + '/' + str(line) + '-feature.txt', 'a+') as fw:
    path = './' + day + '/' + str(line) + '-station.txt'
    data = pd.read_table(path, header=None, sep=',', encoding='utf-8')
    data.columns = ["O_UP", "Source_Station", "Target_Station", "Distance", 'Diff_Time']
    path1 = './' + day + '/' + str(line) + '-v.txt';
    busmaxv = pd.read_table(path1, header=None, sep=',', encoding='utf-8')
    busmaxv.columns = ['O_TIME', "O_UP", "Source_Station", "Target_Station", "MaxV"]
    busmaxv['O_TIME'] = pd.to_datetime(busmaxv['O_TIME'],format='%Y-%m-%d %H:%M:%S')
    data['O_TIME'] = busmaxv['O_TIME']

    # read -station

    # 8 weekday
    data['weekday'] =  busmaxv.iloc[0]['O_TIME'].weekday()
    # 9 is_workday
    data['is_workday'] = data['weekday'].apply(lambda x: 0 if x>=5 else 1)

    weat = weather[(weather['days'] == '2017-10-' + day)].iloc[0]
    # 10-14 dws nws dts nts is_rain
    data['dws'] = weat['dws_onehot']
    data['nws'] = weat['nws_onehot']
    data['dts'] = weat['dts']
    data['nts'] = weat['nts']
    data['is_rain'] = weat['is_rain']

    data['hour'] = data['O_TIME'].apply(lambda x: x.hour)
    # 7 is_peek
    data['is_peek'] = data['hour'].apply(lambda x: 1 if ((x>=7 and x <9) or (x>=16 and x<19)) else 0)
    # 15 max_v
    data['max_v'] = busmaxv['MaxV']

    # history
    # 16 aver_diff

    tmp = data.apply(lambda x: find_history_dist(line,x['is_rain'], x['is_workday'],x['is_peek'],x['O_UP'], x['Source_Station'], x['Target_Station']), axis=1).reset_index()

    data['h_aver_diff'] = tmp['Diff_Time']
    # 17 aver_d
    data['h_aver_d'] = tmp['Distance']
    # 18 aver_v
    data['h_aver_v'] = 3600 * (data['h_aver_d'] / data['h_aver_diff'] ) # need read from day-station


#     # 前一站平均速度 need read from day-station 当前数据的上一行
#     h1 = find_history(is_rain, is_workday, is_peek, line, on, start_station - 1, next_station - 1)
#     # 19 last_aver_v
#     last_aver_v = h1['Distance'].mean() / h1['Diff_Time'].mean()

    # 20 is block up route

    # 21 dynamic



In [143]:
#read station-station
def read_station():
    bus = pd.DataFrame()
    for i in range(line.shape[0]):
        num = line.iloc[i]

        path = './station/'+str(num)+'-station.txt';
        if os.path.exists(path):
            bus1 = pd.read_table(path,header=None,sep=',',encoding='utf-8')
            bus1.columns=["O_UP","Source_Station","Target_Station","Distance",'Diff_Time']
            bus1['O_LINENO'] = num
            bus = pd.concat([bus,bus1])
    bus.groupby(['O_LINENO','O_UP']).apply(lambda x:x.sort_values(by='Station', ascending=True))
    return bus

In [220]:
line = '652'
day = '01'

d1 =  datetime.datetime.now()

path = './' + day + '/' + str(line) + '-station.txt'
data = pd.read_table(path, header=None, sep=',', encoding='utf-8')
data.columns = ["O_UP", "Source_Station", "Target_Station", "Distance", 'Diff_Time']
path1 = './' + day + '/' + str(line) + '-v.txt';
busmaxv = pd.read_table(path1, header=None, sep=',', encoding='utf-8')
busmaxv.columns = ['O_TIME', "O_UP", "Source_Station", "Target_Station", "MaxV"]
busmaxv['O_TIME'] = pd.to_datetime(busmaxv['O_TIME'],format='%Y-%m-%d %H:%M:%S')
data['O_TIME'] = busmaxv['O_TIME']

# read -station

# 8 weekday
data['weekday'] =  busmaxv.iloc[0]['O_TIME'].weekday()
# 9 is_workday
data['is_workday'] = data['weekday'].apply(lambda x: 0 if x>=5 else 1)

weat = weather[(weather['days'] == '2017-10-' + day)].iloc[0]
# 10-14 dws nws dts nts is_rain
data['dws'] = weat['dws_onehot']
data['nws'] = weat['nws_onehot']
data['dts'] = weat['dts']
data['nts'] = weat['nts']
data['is_rain'] = weat['is_rain']

data['hour'] = data['O_TIME'].apply(lambda x: x.hour)
# 7 is_peek
data['is_peek'] = data['hour'].apply(lambda x: 1 if ((x>=7 and x <9) or (x>=16 and x<19)) else 0)
# 15 max_v
data['max_v'] = busmaxv['MaxV']

d2 =  datetime.datetime.now()
print('time1',(d2 - d1).microseconds)
# history
# 16 aver_diff

tmp = data.apply(lambda x: find_history_dist(line,x['is_rain'], x['is_workday'],x['is_peek'],x['O_UP'], x['Source_Station'], x['Target_Station']), axis=1).reset_index()

data['h_aver_diff'] = tmp['Diff_Time']
# 17 aver_d
data['h_aver_d'] = tmp['Distance']
# 18 aver_v
def averV(d,n):
    if (int(d)==-1 or int(n)==-1):
        print(d,n)
        return -1
    else :
        return 3600 * d / n
data['h_aver_v'] = data.apply(lambda x: averV(x['h_aver_d'],x['h_aver_diff']), axis=1)
#3600 * (data / data['h_aver_diff'] ) # need read from day-station

d3 =  datetime.datetime.now()
print('time2',(d3 - d2).microseconds)
# 前一站平均速度 need read from day-station 当前数据的上一行
# # 19 last_aver_v
# tmp = data.apply(lambda x: find_history_dist(line,x['is_rain'], x['is_workday'],x['is_peek'],x['O_UP'], x['Source_Station']-1, x['Target_Station']-1), axis=1).reset_index()
# data['last_aver_v'] =  tmp['Distance'] /  tmp['Diff_Time']

# d4 =  datetime.datetime.now()
# print('time3',(d4 - d3).microseconds)
data

time1 180197
time2 220867


O_UP  Source_Station  Target_Station  Distance  Diff_Time  \
0         1               1               2  0.489291         46   
1         1               2               3  2.110603        184   
2         1               3               4  0.980013        120   
3         1               4               5  0.409648         81   
4         1               5               6  0.368643         79   
5         1               6               7  0.754366         90   
6         1               7               8  0.933472        180   
7         1               8               9  0.724700        111   
8         1               9              10  0.555195        120   
9         1              10              11  1.560623        319   
10        1              11              12  0.590388        100   
11        1              12              13  0.575100        150   
12        1              13              14  0.632159        130   
13        1              14              15  1.273851        201   
14        1              15              16  0.678831         79   
15        1              16              17  0.533903        180   
16        1              17              18  0.846556        210   
17        1              18              19  0.755436        110   
18        1              19              20  2.268548        196   
19        1              20              21  0.453965         60   
20        1              21              22  0.597715         79   
21        1              22              23  1.318292        121   
22        1              23              24  0.509879         59   
23        1              24              25  0.851859         90   
24        1              25              26  1.207652        121   
25        1              26              27  1.048559        110   
26        1              27              28  0.740462         89   
27        1              28              29  0.446324        100   
28        1              29              30  0.433230         60   
29        1              30              31  0.691087        130   
...     ...             ...             ...       ...        ...   
13537     1              54              55  0.499784         80   
13538     1              55              56  0.786999        121   
13539     1              56              57  1.010670        119   
13540     1              57              58  0.597251         50   
13541     1              58              59  0.848625         50   
13542     1              59              60  0.770031         50   
13543     1              60              61  1.299192         81   
13544     1              61              62  0.831234         49   
13545     1              62              63  1.021611         90   
13546     1              63              64  0.596810         70   
13547     1              64              65  0.590047         61   
13548     1              65              66  0.961006        100   
13549     1              66              67  0.435649         39   
13550     1              67              68  0.958256        210   
13551     1              68              69  0.260610         30   
13552     1              69              70  0.755515        140   
13553     1              70              71  0.444919         80   
13554     1              71              72  0.683829         70   
13555     1              72              73  0.625389        100   
13556     1              73              74  1.922762        180   
13557     1              74              75  0.783042         61   
13558     1              75              76  0.373867         49   
13559     1              76              77  2.410436        135   
13560     1              77              78  0.885573         49   
13561     1              78              79  0.929937         50   
13562     1              79              80  1.122925         70   
13563     1              80              81  0.699690         6

In [102]:
def find_history2(is_rain,is_workday,is_peek,buss,busv):
    #buss = buss[(buss['Distance'] < 10) & (buss['Diff_Time'] < 1000)]
    if is_rain ==0 and is_workday ==1 :
        days = ['02','03','04','05','06','11','12','13','16','19','20','23','24','25','26','27','30','31']
    elif is_rain ==0 and is_workday ==0 :
        days = ['01','15','22','28','19']
    elif is_rain ==1 and is_workday ==1 :
        days = ['09','10','17','18']
    else :
        days = ['07','08','14','21']
    if is_peek == 1:
        time_hour = [('07','09'),('16','19')]
    else :
        time_hour = [('06','07'),('09','16'),('19','23')]
    bus = pd.DataFrame()
#     print(len(days))
    for i in range(len(days)):
#         d11 = datetime.datetime.now()
        day = days[i]
        for j in range(len(time_hour)):
            start = '2017-10-' + day + ' ' + time_hour[j][0] + ':00:00'
            end =  '2017-10-' + day + ' ' + time_hour[j][1] + ':00:00'
                
            index = (busv['O_TIME']>=start)&(busv['O_TIME']<end)#&(busv['O_UP']==on)&(busv['Source_Station']==start_station)&(busv['Target_Station']==next_station)
#             print(start,end)
            b = buss[index]
            
#             b['O_TIME'] = busv[index]['O_TIME']
            bus = pd.concat([bus,b])
#         d3 = datetime.datetime.now()
#         print('time2',(d3 - d11).microseconds)
    return bus

In [13]:
d1 = datetime.datetime.now()
b = find_history2(0,0,1,652,1,9,10)
d2 =  datetime.datetime.now()
print('time',(d2 - d1).microseconds)
# print(3600*b['Distance'].mean()/b['Diff_Time'].mean())

time1 80986
time2 20487
time1 42148
time2 13189
time1 40850
time2 13689
time1 52301
time2 14037


/home/b418-xiwei/anaconda3/envs/dl/lib/python3.6/site-packages/ipykernel_launcher.py:35: UserWarning: Boolean Series key will be reindexed to match DataFrame index.


time1 51510
time2 13745
time1 23086
time2 13429
time 408063


In [409]:
d1 = datetime.datetime.now()
get_feature(bus1,652)
d2 =  datetime.datetime.now()
print('time6',(d2 - d1).seconds)

time6 222


In [50]:
num=652
d1 =  datetime.datetime.now()
busV = pd.DataFrame()
busS = pd.DataFrame()
for d in range(1, 25):
    if d < 10:
        day = '0' + str(d)
    else:
        day = str(d)
    path1 = './' + day + '/' + str(num) +'-v.txt';
    path2 = './' + day + '/' + str(num) +'-station.txt';
    if os.path.exists(path1) and os.path.exists(path2):
#         print(path1,path2)
        busv = pd.read_table(path1,header=None,sep=',',encoding='utf-8')
        busv.columns=['O_TIME',"O_UP","Source_Station","Target_Station","MaxV"]
        buss = pd.read_table(path2,header=None,sep=',',encoding='utf-8')
        buss.columns=["O_UP","Source_Station","Target_Station","Distance",'Diff_Time']
#         buss = buss[(buss['Distance'] < 10) & (buss['Diff_Time'] < 1000)]
#         print(busv.shape,buss.shape)
        busV = pd.concat([busV,busv])
        busS = pd.concat([busS,buss])
d2 =  datetime.datetime.now()
print('time',(d2 - d1).microseconds)       


time 345291


In [72]:
d1 = datetime.datetime.now()
b = find_history2(0,1,1,busS,busV)
d2 =  datetime.datetime.now()
print('time',(d2 - d1).microseconds)
b = b[(b['Distance'] < 10) & (b['Diff_Time'] < 1000)]
b.groupby(['O_UP','Source_Station','Target_Station']).mean()
d3 =  datetime.datetime.now()
print('time',(d3 - d2).microseconds)


time 101674
time 8115


In [410]:
import pickle
# num=652
def history(num):
    d1 =  datetime.datetime.now()
    busV = pd.DataFrame()
    busS = pd.DataFrame()
    for d in range(9, 32):
        if d < 10:
            day = '0' + str(d)
        else:
            day = str(d)
        path1 = './' + day + '/' + str(num) +'-v.txt';
        path2 = './' + day + '/' + str(num) +'-station.txt';
        if os.path.exists(path1) and os.path.exists(path2):
#             print(path1,path2)#./24/621-v.txt ./24/621-station.txt
            busv = pd.read_table(path1,header=None,sep=',',encoding='utf-8')
            if d >= 25 :
                busv.columns=['O_TERMINALNO','O_TIME',"O_UP","Source_Station","Target_Station","MaxV"]
            else :
                busv.columns=['O_TIME',"O_UP","Source_Station","Target_Station","MaxV"]
            buss = pd.read_table(path2,header=None,sep=',',encoding='utf-8')
            buss.columns=["O_UP","Source_Station","Target_Station","Distance",'Diff_Time']
            buss['O_TIME'] = busv['O_TIME']
            busV = pd.concat([busV,busv])
            busS = pd.concat([busS,buss])
    
    if (busV.shape[0]>0 and busS.shape[0]>0):
        for is_rain in range(0,2):
            for is_work in range(0,2):
                for is_peek in range(0,2):
                    b = find_history2(is_rain,is_work,is_peek,busS,busV)
                    b = b[(b['Distance'] < 10) & (b['Diff_Time'] < 1000)]
#                     b = b.groupby(['O_UP','Source_Station','Target_Station']).mean()
                    with open('./history/'+str(num)+'_'+str(is_rain)+'_'+str(is_work)+'_'+str(is_peek)+'.txt', 'wb') as data_file:
                        pickle.dump(b, data_file)
    d2 =  datetime.datetime.now()
    print('time',(d2 - d1).microseconds)

In [409]:
path1 = './25/621-v.txt'
path2 = './25/621-station.txt'
num = 621
busV = pd.DataFrame()
busS = pd.DataFrame()
if os.path.exists(path1) and os.path.exists(path2):
    print(path1,path2)#./24/621-v.txt ./24/621-station.txt
    busv = pd.read_table(path1,header=None,sep=',',encoding='utf-8')
    busv.columns=['O_TERMINALNO','O_TIME',"O_UP","Source_Station","Target_Station","MaxV"]
    buss = pd.read_table(path2,header=None,sep=',',encoding='utf-8')
    buss.columns=["O_UP","Source_Station","Target_Station","Distance",'Diff_Time']
    buss['O_TIME'] = busv['O_TIME']
    busV = pd.concat([busV,busv])
    busS = pd.concat([busS,buss])

if (busV.shape[0]>0 and busS.shape[0]>0):
    for is_rain in range(0,2):
        for is_work in range(0,2):
            for is_peek in range(0,2):
#                 print(is_rain,is_work,is_peek)
                b = find_history2(is_rain,is_work,is_peek,busS,busV)
                b = b[(b['Distance'] < 10) & (b['Diff_Time'] < 1000)]
#                 b.groupby(['O_UP','Source_Station','Target_Station']).mean()
                with open('./data/'+str(num)+'_'+str(is_rain)+'_'+str(is_work)+'_'+str(is_peek)+'.txt', 'wb') as data_file:
                    pickle.dump(b, data_file)

./25/621-v.txt ./25/621-station.txt


In [411]:
#history
# line = pd.DataFrame()
# for d in range(25, 32):
#     if d < 10:
#         day = '0' + str(d)
#     else:
#         day = str(d)

#     train = pd.read_csv("./data/train201710"+day+".csv", sep=",")
#     train['O_TIME'] = pd.to_datetime('2017-10-' + day + ' ' + train['O_TIME'], format='%Y-%m-%d %H:%M:%S')
#     train = train.groupby(['O_LINENO', 'O_TERMINALNO']).apply(lambda x: x.sort_values(by='O_TIME', ascending=True))
    
#     line = pd.concat([line,train['O_LINENO']])
# line = line.drop_duplicates()
# with open('./history/line_test.txt', 'wb') as data_file:
#     pickle.dump(line, data_file)
with open('./data/line_test.txt', 'rb') as data_file:
    line = pickle.load(data_file)
with open('./data/line_test.txt', 'rb') as data_file:
    line1 = pickle.load(data_file)
    line = pd.concat([line,line1])
line = line.drop_duplicates()
line.columns=['line']
print(line.shape)
for i in range(line.shape[0]):
    l = int(line['line'].iloc[i])
    history(l)
    print(l,"finished")

(564, 1)
time 877892
1 finished
time 62314
3 finished
time 375888
5 finished
time 758905
8 finished
time 177393
9 finished
time 797343
10 finished
time 820075
12 finished
time 754382
13 finished
time 379965
15 finished
time 95255
20 finished
time 299556
22 finished
time 166990
24 finished
time 512434
27 finished
time 961884
28 finished
time 137257
30 finished
time 843242
31 finished
time 359979
32 finished
time 954482
34 finished
time 464157
35 finished
time 888293
37 finished
time 135618
42 finished
time 696484
45 finished
time 19015
47 finished
time 201629
48 finished
time 140565
50 finished
time 527039
52 finished
time 493792
92 finished
time 687394
93 finished
time 874609
95 finished
time 82454
96 finished
time 887996
97 finished
time 434734
133 finished
time 381640
153 finished
time 56406
157 finished
time 994612
161 finished
time 1087
162 finished
time 801224
163 finished
time 628983
168 finished
time 676
172 finished
time 810854
174 finished
time 213242
175 finished
time 812919


time 780203
830 finished
time 908399
831 finished
time 408823
832 finished
time 432133
835 finished
time 17499
836 finished
time 800468
837 finished
time 678202
838 finished
time 400826
840 finished
time 248992
841 finished
time 952169
842 finished
time 165223
845 finished
time 888905
846 finished
time 147045
847 finished
time 882313
849 finished
time 575055
850 finished
time 136582
851 finished
time 510055
852 finished
time 849101
855 finished
time 749296
856 finished
time 745053
857 finished
time 998648
858 finished
time 311041
859 finished
time 378623
860 finished
time 719692
861 finished
time 681325
862 finished
time 990070
863 finished
time 260698
865 finished
time 514396
866 finished
time 436343
867 finished
time 908394
868 finished
time 469938
869 finished
time 927229
870 finished
time 256019
871 finished
time 73322
872 finished
time 899344
878 finished
time 758917
879 finished
time 1603
888 finished
time 920
891 finished
time 450123
901 finished
time 546708
902 finished
time 91

In [450]:
test = pd.read_csv("./toBePredicted_528_segment.csv", sep=",")
test['DATA'] = pd.to_datetime('2017-'+test['DATA'],format='%Y-%m-%d %H:%M:%S')
test['realTime'] = pd.to_datetime(test['realTime'],format='%Y-%m-%d %H:%M:%S')
# 8 weekday
day = str(25)
test1 = test[test['DATA']=='2017-10-'+day]
test1
# train = train.groupby(['O_LINENO', 'O_TERMINALNO']).apply(lambda x:x.sort_values(by='O_TIME', ascending=True))

Unnamed: 0       DATA  LATITUDE  LINE  LONGITUDE  TERMINALNO  UP  \
138              0 2017-10-25   39.1115   668    117.230      902903   1   
139              0 2017-10-25   39.1115   668    117.230      902903   1   
140              0 2017-10-25   39.1115   668    117.230      902903   1   
141              0 2017-10-25   39.1115   668    117.230      902903   1   
142              0 2017-10-25   39.1115   668    117.230      902903   1   
143              0 2017-10-25   39.1115   668    117.230      902903   1   
144              0 2017-10-25   39.1115   668    117.230      902903   1   
145              0 2017-10-25   39.1115   668    117.230      902903   1   
146              0 2017-10-25   39.1115   668    117.230      902903   1   
147              0 2017-10-25   39.1115   668    117.230      902903   1   
148              0 2017-10-25   39.1115   668    117.230      902903   1   
149              0 2017-10-25   39.1115   668    117.230      902903   1   
150              0 2017-10-25   39.1115   668    117.230      902903   1   
151              0 2017-10-25   39.1115   668    117.230      902903   1   
152              0 2017-10-25   39.1115   668    117.230      902903   1   
153              0 2017-10-25   39.1115   668    117.230      902903   1   
154              0 2017-10-25   39.1115   668    117.230      902903   1   
363              0 2017-10-25   39.0848   866    117.179      905578   0   
364              0 2017-10-25   39.0848   866    117.179      905578   0   
365              0 2017-10-25   39.0848   866    117.179      905578   0   
366              0 2017-10-25   39.0848   866    117.179      905578   0   
367              0 2017-10-25   39.0848   866    117.179      905578   0   
368              0 2017-10-25   39.0848   866    117.179      905578   0   
369              0 2017-10-25   39.0848   866    117.179      905578   0   
370              0 2017-10-25   39.0848   866    117.179      905578   0   
371              0 2017-10-25   39.0848   866    117.179      905578   0   
372              0 2017-10-25   39.0848   866    117.179      905578   0   
373              0 2017-10-25   39.0848   866    117.179      905578   0   
374              0 2017-10-25   39.0848   866    117.179      905578   0   
375              0 2017-10-25   39.0848   866    117.179      905578   0   
...            ...        ...       ...   ...        ...         ...  ..   
958865           0 2017-10-25   39.1191     3    117.182      932509   1   
958866           0 2017-10-25   39.1191     3    117.182      932509   1   
958867           0 2017-10-25   39.1191     3    117.182      932509   1   
958882           0 2017-10-25   39.0605   185    117.406      905674   0   
958883           0 2017-10-25   39.0605   185    117.406      905674   0   
958884           0 2017-10-25   39.0605   185    117.406      905674   0   
958885           0 2017-10-25   39.0605   185    117.406      905674   0   
958886           0 2017-10-25   39.0605   185    117.406      905674   0   
958887           0 2017-10-25   39.0605   185    117.406      905674   0   
958888           0 2017-10-25   39.0605   185    117.406      905674   0   
958889           0 2017-10-25   39.0605   185    117.406      905674   0   
958890           0 2017-10-25   39.0605   185    117.406      905674   0   
958891           0 2017-10-25   39.0605   185    117.406      905674   0   
958892           0 2017-10-25   39.0605   185    117.406      905674   0   
958893           0 2017-10-25   39.0605   185    117.406      905674   0   
958894           0 2017-10-25   39.0605   185    117.406      905674   0   
958895           0 2017-10-25   39.0605   185    117.406      905674   0   
958896           0 2017-10-25   39.0605   185    117.406      905674   0   
958897           0 2017-10-25   39.0605   185    117.406      905674   0   
959046           0 2017-10-25   39.0322   133    117.658      905307   1   
959047           0 2017-10-25   39.0322   133    117.658

In [452]:
d1 =  datetime.datetime.now()
# 8 weekday
test1['weekday'] = test1['DATA'].dt.weekday

# 9 is_workday
test1['is_workday'] = test1['weekday'].apply(lambda x: 0 if x>=5 else 1)

weat = weather[(weather['days'] == '2017-10-' + day)].iloc[0]
# 10-14 dws nws dts nts is_rain
test1['dws'] = weat['dws_onehot']
test1['nws'] = weat['nws_onehot']
test1['dts'] = weat['dts']
test1['nts'] = weat['nts']
test1['is_rain'] = weat['is_rain']
#6 hour
test1['hour'] = test1['realTime'].apply(lambda x: x.hour)
# 7 is_peek
test1['is_peek'] = test1['hour'].apply(lambda x: 1 if ((x>=7 and x <9) or (x>=16 and x<19)) else 0)

# 15 max_v ?是否有用 存疑 test数据无法捕捉 置为-1 
# def getV(day,line,time,term):  
#     path1 = './' + day + '/' + str(line) + '-v.txt';
#     if os.path.exists(path1):
#         busmaxv = pd.read_table(path1, header=None, sep=',', encoding='utf-8')
#         busmaxv.columns = ['O_TERMINALNO','O_TIME', "O_UP", "Source_Station", "Target_Station", "MaxV"]
#         busmaxv['O_TIME'] = pd.to_datetime(busmaxv['O_TIME'],format='%Y-%m-%d %H:%M:%S')
#         b = busmaxv[(busmaxv['O_TIME']<time)&(busmaxv['O_TERMINALNO']==term)]
#         if b.shape[0] > 0:
#             return b.iloc[-1]['MaxV']
#         else:
#             return -1
# test1['max_v'] = test1.apply(lambda x:getV(day,x['LINE'],x['realTime'],x['TERMINALNO']),axis=1)
test1['max_v'] = -1

def read_station(line,on,start,end):
    path = './station/'+str(line)+'-dist.txt'
    if os.path.exists(path):
        bus1 = pd.read_table(path,header=None,sep=',',encoding='utf-8')
        bus1.columns=["O_UP","Source_Station","Target_Station","Distance"]
        b = bus1[(bus1['O_UP']==on)&(bus1['Source_Station']==start)&(bus1['Target_Station']==end)]
        if b.shape[0] > 0:
            return b.iloc[0]['Distance']
        else :
            return -1
    else :
        return -1
test1['Distance'] = test1.apply(lambda x: read_station(x['LINE'],x['UP'], x['pred_start_stop_ID'], x['pred_end_stop_ID']), axis=1)

d2 =  datetime.datetime.now()
print('time',(d2 - d1).microseconds)

tmp = test1.apply(lambda x: find_history_dist(x['LINE'],x['is_rain'], x['is_workday'],x['is_peek'],x['UP'], x['pred_start_stop_ID'], x['pred_end_stop_ID'],str(x['realTime'])), axis=1)

test1['h_aver_diff'] = tmp['Diff_Time']
# 17 aver_d
test1['h_aver_d'] = tmp['Distance']
# 18 aver_v
def averV(d,n):
    if (int(d)==-1 or int(n)==-1):
#         print(d,n)
        return -1
    else :
        return 3600 * d / n
test1['h_aver_v'] = test1.apply(lambda x: averV(x['h_aver_d'],x['h_aver_diff']), axis=1)

d3 =  datetime.datetime.now()
print('time',(d3 - d2).microseconds)

test1

/home/b418-xiwei/anaconda3/envs/dl/lib/python3.6/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  This is separate from the ipykernel package so we can avoid doing imports until
/home/b418-xiwei/anaconda3/envs/dl/lib/python3.6/site-packages/ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
/home/b418-xiwei/anaconda3/envs/dl/lib/python3.6/site-packages/ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[r

time 525457


/home/b418-xiwei/anaconda3/envs/dl/lib/python3.6/site-packages/ipykernel_launcher.py:54: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/home/b418-xiwei/anaconda3/envs/dl/lib/python3.6/site-packages/ipykernel_launcher.py:56: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0
-1.0 -1.0


/home/b418-xiwei/anaconda3/envs/dl/lib/python3.6/site-packages/ipykernel_launcher.py:64: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


Unnamed: 0       DATA  LATITUDE  LINE  LONGITUDE  TERMINALNO  UP  \
138              0 2017-10-25   39.1115   668    117.230      902903   1   
139              0 2017-10-25   39.1115   668    117.230      902903   1   
140              0 2017-10-25   39.1115   668    117.230      902903   1   
141              0 2017-10-25   39.1115   668    117.230      902903   1   
142              0 2017-10-25   39.1115   668    117.230      902903   1   
143              0 2017-10-25   39.1115   668    117.230      902903   1   
144              0 2017-10-25   39.1115   668    117.230      902903   1   
145              0 2017-10-25   39.1115   668    117.230      902903   1   
146              0 2017-10-25   39.1115   668    117.230      902903   1   
147              0 2017-10-25   39.1115   668    117.230      902903   1   
148              0 2017-10-25   39.1115   668    117.230      902903   1   
149              0 2017-10-25   39.1115   668    117.230      902903   1   
150              0 2017-10-25   39.1115   668    117.230      902903   1   
151              0 2017-10-25   39.1115   668    117.230      902903   1   
152              0 2017-10-25   39.1115   668    117.230      902903   1   
153              0 2017-10-25   39.1115   668    117.230      902903   1   
154              0 2017-10-25   39.1115   668    117.230      902903   1   
363              0 2017-10-25   39.0848   866    117.179      905578   0   
364              0 2017-10-25   39.0848   866    117.179      905578   0   
365              0 2017-10-25   39.0848   866    117.179      905578   0   
366              0 2017-10-25   39.0848   866    117.179      905578   0   
367              0 2017-10-25   39.0848   866    117.179      905578   0   
368              0 2017-10-25   39.0848   866    117.179      905578   0   
369              0 2017-10-25   39.0848   866    117.179      905578   0   
370              0 2017-10-25   39.0848   866    117.179      905578   0   
371              0 2017-10-25   39.0848   866    117.179      905578   0   
372              0 2017-10-25   39.0848   866    117.179      905578   0   
373              0 2017-10-25   39.0848   866    117.179      905578   0   
374              0 2017-10-25   39.0848   866    117.179      905578   0   
375              0 2017-10-25   39.0848   866    117.179      905578   0   
...            ...        ...       ...   ...        ...         ...  ..   
958865           0 2017-10-25   39.1191     3    117.182      932509   1   
958866           0 2017-10-25   39.1191     3    117.182      932509   1   
958867           0 2017-10-25   39.1191     3    117.182      932509   1   
958882           0 2017-10-25   39.0605   185    117.406      905674   0   
958883           0 2017-10-25   39.0605   185    117.406      905674   0   
958884           0 2017-10-25   39.0605   185    117.406      905674   0   
958885           0 2017-10-25   39.0605   185    117.406      905674   0   
958886           0 2017-10-25   39.0605   185    117.406      905674   0   
958887           0 2017-10-25   39.0605   185    117.406      905674   0   
958888           0 2017-10-25   39.0605   185    117.406      905674   0   
958889           0 2017-10-25   39.0605   185    117.406      905674   0   
958890           0 2017-10-25   39.0605   185    117.406      905674   0   
958891           0 2017-10-25   39.0605   185    117.406      905674   0   
958892           0 2017-10-25   39.0605   185    117.406      905674   0   
958893           0 2017-10-25   39.0605   185    117.406      905674   0   
958894           0 2017-10-25   39.0605   185    117.406      905674   0   
958895           0 2017-10-25   39.0605   185    117.406      905674   0   
958896           0 2017-10-25   39.0605   185    117.406      905674   0   
958897           0 2017-10-25   39.0605   185    117.406      905674   0   
959046           0 2017-10-25   39.0322   133    117.658      905307   1   
959047           0 2017-10-25   39.0322   133    117.658

In [412]:
def find_history_dist(num,is_rain,is_workday,is_peek,on,start_station,next_station,time):
    with open('./history/'+str(num)+'_'+str(is_rain)+'_'+str(is_workday)+'_'+str(is_peek)+'.txt', 'rb') as data_file:
        b = pickle.load(data_file).reset_index()
#         b['O_TIME'] = pd.to_datetime(b['O_TIME'],format='%Y-%m-%d %H:%M:%S')
        b = b[(b['O_TIME']<time)]
        b = b.groupby(['O_UP','Source_Station','Target_Station']).mean().reset_index()
        # 	O_UP 	Source_Station 	Target_Station
        b = b[(b['O_UP']==on)&(b['Source_Station']==start_station)&(b['Target_Station']==next_station)]
        if b.shape[0] > 0:
            return b.iloc[0]
        else :
            dic = {'Distance':[-1],'Diff_Time':[-1]}
            x = pd.DataFrame(dic)
            return x.iloc[0]

In [152]:
data

O_UP  Source_Station  Target_Station  Distance  Diff_Time  \
0         1               1               2  0.489291         46   
1         1               2               3  2.110603        184   
2         1               3               4  0.980013        120   
3         1               4               5  0.409648         81   
4         1               5               6  0.368643         79   
5         1               6               7  0.754366         90   
6         1               7               8  0.933472        180   
7         1               8               9  0.724700        111   
8         1               9              10  0.555195        120   
9         1              10              11  1.560623        319   
10        1              11              12  0.590388        100   
11        1              12              13  0.575100        150   
12        1              13              14  0.632159        130   
13        1              14              15  1.273851        201   
14        1              15              16  0.678831         79   
15        1              16              17  0.533903        180   
16        1              17              18  0.846556        210   
17        1              18              19  0.755436        110   
18        1              19              20  2.268548        196   
19        1              20              21  0.453965         60   
20        1              21              22  0.597715         79   
21        1              22              23  1.318292        121   
22        1              23              24  0.509879         59   
23        1              24              25  0.851859         90   
24        1              25              26  1.207652        121   
25        1              26              27  1.048559        110   
26        1              27              28  0.740462         89   
27        1              28              29  0.446324        100   
28        1              29              30  0.433230         60   
29        1              30              31  0.691087        130   
...     ...             ...             ...       ...        ...   
13537     1              54              55  0.499784         80   
13538     1              55              56  0.786999        121   
13539     1              56              57  1.010670        119   
13540     1              57              58  0.597251         50   
13541     1              58              59  0.848625         50   
13542     1              59              60  0.770031         50   
13543     1              60              61  1.299192         81   
13544     1              61              62  0.831234         49   
13545     1              62              63  1.021611         90   
13546     1              63              64  0.596810         70   
13547     1              64              65  0.590047         61   
13548     1              65              66  0.961006        100   
13549     1              66              67  0.435649         39   
13550     1              67              68  0.958256        210   
13551     1              68              69  0.260610         30   
13552     1              69              70  0.755515        140   
13553     1              70              71  0.444919         80   
13554     1              71              72  0.683829         70   
13555     1              72              73  0.625389        100   
13556     1              73              74  1.922762        180   
13557     1              74              75  0.783042         61   
13558     1              75              76  0.373867         49   
13559     1              76              77  2.410436        135   
13560     1              77              78  0.885573         49   
13561     1              78              79  0.929937         50   
13562     1              79              80  1.122925         70   
13563     1              80              81  0.699690         6

In [491]:
with open('./data/train.txt', 'rb') as data_file:
    line = pickle.load(data_file)
line.columns

Index(['O_UP', 'Source_Station', 'Target_Station', 'Distance', 'Diff_Time',
       'O_TIME', 'O_LINENO', 'aver_v', 'hour', 'is_peek', 'weekday',
       'is_workday', 'dws', 'nws', 'dts', 'nts', 'is_rain', 'max_v',
       'h_aver_diff', 'h_aver_d', 'h_aver_v'],
      dtype='object')

In [492]:
def idfeature(a,b,c,d):
    if c < 10:
        c = '0'+str(c)
    if d < 10:
        d = '0'+str(d)
    return str(a)+str(b)+str(c)+str(d)
line['ID'] = line.apply(lambda x: idfeature(x['O_LINENO'],x['O_UP'],x['Source_Station'],x['Target_Station']),axis=1)
line = line[['ID','O_LINENO', 'O_UP', 'Source_Station', 'Target_Station', 'Distance',
       'O_TIME', 'aver_v', 'hour', 'is_peek', 'weekday',
       'is_workday', 'dws', 'nws', 'dts', 'nts', 'is_rain', 'max_v',
       'h_aver_diff', 'h_aver_d', 'h_aver_v', 'Diff_Time']]
line

ID  O_LINENO  O_UP  Source_Station  Target_Station      Distance  \
0     80411920       804     1              19              20  61605.795135   
1     80412021       804     1              20              21      0.629329   
2     80412122       804     1              21              22      0.983431   
3     80412223       804     1              22              23      0.690608   
4     80412324       804     1              23              24      0.608654   
5     80412425       804     1              24              25      0.362356   
6     80400203       804     0               2               3      3.064650   
7     80400304       804     0               3               4      0.846219   
8     80400405       804     0               4               5      0.556623   
9     80400506       804     0               5               6      0.582659   
10    80400607       804     0               6               7      1.290634   
11    80400708       804     0               7               8      0.590267   
12    80400809       804     0               8               9      1.402541   
13    80400910       804     0               9              10      0.383117   
14    80401011       804     0              10              11      1.253965   
15    80401112       804     0              11              12      1.246375   
16    80401213       804     0              12              13      1.090529   
17    80401314       804     0              13              14      1.150083   
18    80401415       804     0              14              15      1.945770   
19    80401516       804     0              15              16      1.859327   
20    80401617       804     0              16              17      0.644827   
21    80401718       804     0              17              18      1.593767   
22    80401819       804     0              18              19      2.541232   
23    80401920       804     0              19              20      3.175953   
24    80402021       804     0              20              21      1.803431   
25    80402122       804     0              21              22      1.722122   
26    80402223       804     0              22              23      0.790112   
27    80410102       804     1               1               2      4.142530   
28    80410203       804     1               2               3      0.887927   
29    80410304       804     1               3               4      1.609496   
..         ...       ...   ...             ...             ...           ...   
16  5501210304     55012     1               3               4      4.601789   
17  5501210405     55012     1               4               5      6.609656   
18  5501210506     55012     1               5               6      4.940188   
19  5501210607     55012     1               6               7      5.610340   
20  5501210708     55012     1               7               8      1.720030   
21  5501210809     55012     1               8               9      2.750191   
22  5501200102     55012     0               1               2      7.362725   
23  5501200203     55012     0               2               3      2.722300   
24  5501200304     55012     0               3               4      2.010180   
25  5501200405     55012     0               4               5      5.421040   
26  5501200506     55012     0               5               6      5.100597   
27  5501200607     55012     0               6               7      6.152744   
28  5501200708     55012     0               7               8      1.497825   
29  5501200809     55012     0               8               9      1.402856   
0   5500910102     55009     1               1               2  12314.876199   
1   5500910203     55009     1               2               3      0.477920   
2   5500910304     55009     1               3               4      3.363145   
3   5500910405     55009     1               4               5      8.949766   
4   55009105

In [50]:
#过滤一些 difftime distance
# line = line[(line['Distance']<15)&(line['Diff_Time']<1500)]
# line.shape
# with open('./data/train-id.txt', 'wb') as data_file:
#     pickle.dump(line, data_file)#ID
with open('./data/train-id.txt', 'rb') as data_file:
    line = pickle.load(data_file)

In [11]:
# with open('./data/train-id.txt', 'rb') as data_file:
#     train = pickle.load(data_file)
# from sklearn import preprocessing
# x1 = train['ID'].as_matrix().reshape([-1,1])
# N1 = x1.shape[0]
# with open('./data/test3-id.txt', 'rb') as data_file:
#     test = pickle.load(data_file)
# x2 = test['ID'].as_matrix().reshape([-1,1])
# N2 = x2.shape[0]
# x = np.concatenate((x1,x2))
# x = preprocessing.LabelEncoder().fit_transform(x)
# train['ID'] = x[:N1]
# test['ID'] = x[N1:]
# print(train['ID'].shape,test['ID'].shape)

/home/b418-xiwei/anaconda3/envs/dl/lib/python3.6/site-packages/sklearn/preprocessing/label.py:111: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


KeyboardInterrupt: 

In [45]:
def zuhe(line):
    line['hour'] = line['hour'].astype(str)
    line['weekday'] = line['weekday'].astype(str)
    line['hour_weekday'] = line['hour'] + line['weekday']
    line['hour'] = line['hour'].astype(int)
    line['weekday'] = line['weekday'].astype(int)
    line['hour_weekday'] = line['hour_weekday'].astype(int)
    return line

# from sklearn import preprocessing
# x = line['ID'].values.reshape([-1,1])
# x = preprocessing.LabelEncoder().fit_transform(x)
# x.shape

In [ ]:
lgb_train  = lgb.Dataset(line[col].values, line['Diff_Time'].values)#feature_name=col,categorical_feature=['ID']
params = {'min_data_in_leaf': 10, 
          'feature_fraction': 0.95, 
          'lambda_l1': 25, 
          'lambda_l2': 0.5,
          'num_leaves':150, 
          'max_depth':8,
          'seed':2018,
          'num_threads':20,
          'subsample':0.9,
          'n_estimators':50000,
          'learning_rate': 0.01,
          'objective':'regression_l2',  
          'metric':'rmse'}
lgb.cv(param, line, nfold=5, early_stopping_rounds=200,)

In [66]:
with open('./data/train-id.txt', 'rb') as data_file:
    line = pickle.load(data_file)
    line = zuhe(line)
line = line[(line['Diff_Time']<900)]
from sklearn.utils import shuffle
line['ID'] = line['ID'].astype('category') 
line = shuffle(line)
train_num = int(0.9 * line.shape[0])
train = line[:train_num]
#!
dev = line[train_num:]
print(train.shape)
print(dev.shape)

(12476814, 23)
(1386313, 23)


In [22]:
col = [c for c in train if
       c not in ['O_LINENO', 'O_UP', 'Source_Station', 'Target_Station','O_TIME', 'aver_v','max_v', 'Diff_Time']]
col

['ID',
 'Distance',
 'hour',
 'is_peek',
 'weekday',
 'is_workday',
 'dws',
 'nws',
 'dts',
 'nts',
 'is_rain',
 'h_aver_diff',
 'h_aver_d',
 'h_aver_v',
 'hour_weekday']

In [67]:
import lightgbm as lgb
col = [c for c in train if
       c not in ['O_LINENO', 'O_UP', 'Source_Station', 'Target_Station','O_TIME', 'aver_v','max_v', 'Diff_Time']]
X = train[col].values
y = train['Diff_Time'].values
X_tes = dev[col].values
y_tes = dev['Diff_Time'].values
lgb_train  = lgb.Dataset(X, y,)#feature_name=col,categorical_feature=['ID']
lgb_eval = lgb.Dataset(X_tes, y_tes,reference=lgb_train)
params = {'num_leaves':40, 
          'max_depth':8,
          'seed':2018,
          'colsample_bytree':0.8,
          'subsample':0.9,
          'num_threads':20,
          'n_estimators':50000,
          'learning_rate': 0.05,
          'objective':'regression_l2',  
          'metric':'rmse'}
gbm = lgb.train(params, lgb_train,early_stopping_rounds=200,valid_sets=lgb_eval)

/home/b418-xiwei/anaconda3/envs/dl/lib/python3.6/site-packages/lightgbm/engine.py:99: UserWarning: Found `n_estimators` in params. Will use it instead of argument
  warnings.warn("Found `{}` in params. Will use it instead of argument".format(alias))


[1]	valid_0's rmse: 99.2493
Training until validation scores don't improve for 200 rounds.
[2]	valid_0's rmse: 95.7076
[3]	valid_0's rmse: 92.3949
[4]	valid_0's rmse: 89.4389
[5]	valid_0's rmse: 86.6828
[6]	valid_0's rmse: 83.8905
[7]	valid_0's rmse: 81.3349
[8]	valid_0's rmse: 78.9465
[9]	valid_0's rmse: 76.7265
[10]	valid_0's rmse: 74.6439
[11]	valid_0's rmse: 72.7169
[12]	valid_0's rmse: 70.9289
[13]	valid_0's rmse: 69.2669
[14]	valid_0's rmse: 67.7359
[15]	valid_0's rmse: 66.3111
[16]	valid_0's rmse: 64.865
[17]	valid_0's rmse: 63.6459
[18]	valid_0's rmse: 62.5923
[19]	valid_0's rmse: 61.5402
[20]	valid_0's rmse: 60.5587
[21]	valid_0's rmse: 59.6427
[22]	valid_0's rmse: 58.8104
[23]	valid_0's rmse: 58.0359
[24]	valid_0's rmse: 57.3484
[25]	valid_0's rmse: 56.7022
[26]	valid_0's rmse: 56.0863
[27]	valid_0's rmse: 55.5211
[28]	valid_0's rmse: 55.0127
[29]	valid_0's rmse: 54.4572
[30]	valid_0's rmse: 54.0231
[31]	valid_0's rmse: 53.5162
[32]	valid_0's rmse: 53.158
[33]	valid_0's rmse:

[277]	valid_0's rmse: 45.5892
[278]	valid_0's rmse: 45.5882
[279]	valid_0's rmse: 45.5861
[280]	valid_0's rmse: 45.5841
[281]	valid_0's rmse: 45.5814
[282]	valid_0's rmse: 45.5793
[283]	valid_0's rmse: 45.5768
[284]	valid_0's rmse: 45.5753
[285]	valid_0's rmse: 45.574
[286]	valid_0's rmse: 45.5713
[287]	valid_0's rmse: 45.5692
[288]	valid_0's rmse: 45.5684
[289]	valid_0's rmse: 45.567
[290]	valid_0's rmse: 45.5656
[291]	valid_0's rmse: 45.5626
[292]	valid_0's rmse: 45.5615
[293]	valid_0's rmse: 45.5598
[294]	valid_0's rmse: 45.558
[295]	valid_0's rmse: 45.5559
[296]	valid_0's rmse: 45.5547
[297]	valid_0's rmse: 45.553
[298]	valid_0's rmse: 45.551
[299]	valid_0's rmse: 45.5493
[300]	valid_0's rmse: 45.547
[301]	valid_0's rmse: 45.5452
[302]	valid_0's rmse: 45.5435
[303]	valid_0's rmse: 45.5425
[304]	valid_0's rmse: 45.5406
[305]	valid_0's rmse: 45.539
[306]	valid_0's rmse: 45.5378
[307]	valid_0's rmse: 45.5369
[308]	valid_0's rmse: 45.5351
[309]	valid_0's rmse: 45.5341
[310]	valid_0's r

[552]	valid_0's rmse: 45.2691
[553]	valid_0's rmse: 45.268
[554]	valid_0's rmse: 45.2673
[555]	valid_0's rmse: 45.2662
[556]	valid_0's rmse: 45.2646
[557]	valid_0's rmse: 45.264
[558]	valid_0's rmse: 45.2627
[559]	valid_0's rmse: 45.2615
[560]	valid_0's rmse: 45.2607
[561]	valid_0's rmse: 45.2603
[562]	valid_0's rmse: 45.2594
[563]	valid_0's rmse: 45.2591
[564]	valid_0's rmse: 45.2587
[565]	valid_0's rmse: 45.2581
[566]	valid_0's rmse: 45.2577
[567]	valid_0's rmse: 45.2567
[568]	valid_0's rmse: 45.2562
[569]	valid_0's rmse: 45.2546
[570]	valid_0's rmse: 45.2534
[571]	valid_0's rmse: 45.252
[572]	valid_0's rmse: 45.2511
[573]	valid_0's rmse: 45.2496
[574]	valid_0's rmse: 45.2492
[575]	valid_0's rmse: 45.2488
[576]	valid_0's rmse: 45.2486
[577]	valid_0's rmse: 45.2478
[578]	valid_0's rmse: 45.2467
[579]	valid_0's rmse: 45.2456
[580]	valid_0's rmse: 45.2448
[581]	valid_0's rmse: 45.2435
[582]	valid_0's rmse: 45.243
[583]	valid_0's rmse: 45.2421
[584]	valid_0's rmse: 45.2412
[585]	valid_0'

[827]	valid_0's rmse: 45.0877
[828]	valid_0's rmse: 45.0868
[829]	valid_0's rmse: 45.0866
[830]	valid_0's rmse: 45.086
[831]	valid_0's rmse: 45.0853
[832]	valid_0's rmse: 45.085
[833]	valid_0's rmse: 45.0842
[834]	valid_0's rmse: 45.0836
[835]	valid_0's rmse: 45.0833
[836]	valid_0's rmse: 45.0831
[837]	valid_0's rmse: 45.0826
[838]	valid_0's rmse: 45.0825
[839]	valid_0's rmse: 45.0817
[840]	valid_0's rmse: 45.0811
[841]	valid_0's rmse: 45.0808
[842]	valid_0's rmse: 45.0803
[843]	valid_0's rmse: 45.0792
[844]	valid_0's rmse: 45.0789
[845]	valid_0's rmse: 45.0786
[846]	valid_0's rmse: 45.0785
[847]	valid_0's rmse: 45.0778
[848]	valid_0's rmse: 45.0766
[849]	valid_0's rmse: 45.0761
[850]	valid_0's rmse: 45.0756
[851]	valid_0's rmse: 45.0754
[852]	valid_0's rmse: 45.0746
[853]	valid_0's rmse: 45.074
[854]	valid_0's rmse: 45.0735
[855]	valid_0's rmse: 45.0724
[856]	valid_0's rmse: 45.0714
[857]	valid_0's rmse: 45.0706
[858]	valid_0's rmse: 45.07
[859]	valid_0's rmse: 45.0695
[860]	valid_0's

...

[48795]	valid_0's rmse: 43.079
[48796]	valid_0's rmse: 43.0789
[48797]	valid_0's rmse: 43.0789
[48798]	valid_0's rmse: 43.0789
[48799]	valid_0's rmse: 43.0789
[48800]	valid_0's rmse: 43.0789
[48801]	valid_0's rmse: 43.0789
[48802]	valid_0's rmse: 43.0789
[48803]	valid_0's rmse: 43.0789
[48804]	valid_0's rmse: 43.0789
[48805]	valid_0's rmse: 43.0789
[48806]	valid_0's rmse: 43.0789
[48807]	valid_0's rmse: 43.0789
[48808]	valid_0's rmse: 43.0789
[48809]	valid_0's rmse: 43.0789
[48810]	valid_0's rmse: 43.0789
[48811]	valid_0's rmse: 43.0789
[48812]	valid_0's rmse: 43.0789
[48813]	valid_0's rmse: 43.0788
[48814]	valid_0's rmse: 43.0788
[48815]	valid_0's rmse: 43.0788
[48816]	valid_0's rmse: 43.0788
[48817]	valid_0's rmse: 43.0788
[48818]	valid_0's rmse: 43.0788
[48819]	valid_0's rmse: 43.0789
[48820]	valid_0's rmse: 43.0789
[48821]	valid_0's rmse: 43.0789
[48822]	valid_0's rmse: 43.0789
[48823]	valid_0's rmse: 43.0789
[48824]	valid_0's rmse: 43.0788
[48825]	valid_0's rmse: 43.0789
[48826]	v

[49053]	valid_0's rmse: 43.0776
[49054]	valid_0's rmse: 43.0776
[49055]	valid_0's rmse: 43.0776
[49056]	valid_0's rmse: 43.0776
[49057]	valid_0's rmse: 43.0775
[49058]	valid_0's rmse: 43.0775
[49059]	valid_0's rmse: 43.0775
[49060]	valid_0's rmse: 43.0775
[49061]	valid_0's rmse: 43.0774
[49062]	valid_0's rmse: 43.0774
[49063]	valid_0's rmse: 43.0774
[49064]	valid_0's rmse: 43.0774
[49065]	valid_0's rmse: 43.0774
[49066]	valid_0's rmse: 43.0774
[49067]	valid_0's rmse: 43.0774
[49068]	valid_0's rmse: 43.0774
[49069]	valid_0's rmse: 43.0774
[49070]	valid_0's rmse: 43.0774
[49071]	valid_0's rmse: 43.0774
[49072]	valid_0's rmse: 43.0774
[49073]	valid_0's rmse: 43.0773
[49074]	valid_0's rmse: 43.0773
[49075]	valid_0's rmse: 43.0773
[49076]	valid_0's rmse: 43.0773
[49077]	valid_0's rmse: 43.0773
[49078]	valid_0's rmse: 43.0773
[49079]	valid_0's rmse: 43.0773
[49080]	valid_0's rmse: 43.0772
[49081]	valid_0's rmse: 43.0771
[49082]	valid_0's rmse: 43.0771
[49083]	valid_0's rmse: 43.0771
[49084]	

[49311]	valid_0's rmse: 43.0746
[49312]	valid_0's rmse: 43.0746
[49313]	valid_0's rmse: 43.0746
[49314]	valid_0's rmse: 43.0746
[49315]	valid_0's rmse: 43.0746
[49316]	valid_0's rmse: 43.0747
[49317]	valid_0's rmse: 43.0746
[49318]	valid_0's rmse: 43.0746
[49319]	valid_0's rmse: 43.0746
[49320]	valid_0's rmse: 43.0746
[49321]	valid_0's rmse: 43.0746
[49322]	valid_0's rmse: 43.0746
[49323]	valid_0's rmse: 43.0746
[49324]	valid_0's rmse: 43.0747
[49325]	valid_0's rmse: 43.0747
[49326]	valid_0's rmse: 43.0747
[49327]	valid_0's rmse: 43.0747
[49328]	valid_0's rmse: 43.0747
[49329]	valid_0's rmse: 43.0747
[49330]	valid_0's rmse: 43.0747
[49331]	valid_0's rmse: 43.0747
[49332]	valid_0's rmse: 43.0747
[49333]	valid_0's rmse: 43.0746
[49334]	valid_0's rmse: 43.0746
[49335]	valid_0's rmse: 43.0746
[49336]	valid_0's rmse: 43.0746
[49337]	valid_0's rmse: 43.0746
[49338]	valid_0's rmse: 43.0746
[49339]	valid_0's rmse: 43.0746
[49340]	valid_0's rmse: 43.0746
[49341]	valid_0's rmse: 43.0746
[49342]	

[49568]	valid_0's rmse: 43.0722
[49569]	valid_0's rmse: 43.0722
[49570]	valid_0's rmse: 43.0721
[49571]	valid_0's rmse: 43.0721
[49572]	valid_0's rmse: 43.0721
[49573]	valid_0's rmse: 43.0721
[49574]	valid_0's rmse: 43.0721
[49575]	valid_0's rmse: 43.0721
[49576]	valid_0's rmse: 43.0721
[49577]	valid_0's rmse: 43.0721
[49578]	valid_0's rmse: 43.072
[49579]	valid_0's rmse: 43.072
[49580]	valid_0's rmse: 43.072
[49581]	valid_0's rmse: 43.072
[49582]	valid_0's rmse: 43.072
[49583]	valid_0's rmse: 43.0719
[49584]	valid_0's rmse: 43.0719
[49585]	valid_0's rmse: 43.072
[49586]	valid_0's rmse: 43.072
[49587]	valid_0's rmse: 43.072
[49588]	valid_0's rmse: 43.072
[49589]	valid_0's rmse: 43.072
[49590]	valid_0's rmse: 43.072
[49591]	valid_0's rmse: 43.072
[49592]	valid_0's rmse: 43.072
[49593]	valid_0's rmse: 43.072
[49594]	valid_0's rmse: 43.072
[49595]	valid_0's rmse: 43.0719
[49596]	valid_0's rmse: 43.072
[49597]	valid_0's rmse: 43.072
[49598]	valid_0's rmse: 43.072
[49599]	valid_0's rmse: 43

[49827]	valid_0's rmse: 43.0696
[49828]	valid_0's rmse: 43.0696
[49829]	valid_0's rmse: 43.0695
[49830]	valid_0's rmse: 43.0695
[49831]	valid_0's rmse: 43.0695
[49832]	valid_0's rmse: 43.0695
[49833]	valid_0's rmse: 43.0694
[49834]	valid_0's rmse: 43.0694
[49835]	valid_0's rmse: 43.0693
[49836]	valid_0's rmse: 43.0693
[49837]	valid_0's rmse: 43.0693
[49838]	valid_0's rmse: 43.0692
[49839]	valid_0's rmse: 43.0692
[49840]	valid_0's rmse: 43.0693
[49841]	valid_0's rmse: 43.0692
[49842]	valid_0's rmse: 43.0692
[49843]	valid_0's rmse: 43.0692
[49844]	valid_0's rmse: 43.0692
[49845]	valid_0's rmse: 43.0692
[49846]	valid_0's rmse: 43.0691
[49847]	valid_0's rmse: 43.0691
[49848]	valid_0's rmse: 43.0691
[49849]	valid_0's rmse: 43.0691
[49850]	valid_0's rmse: 43.0691
[49851]	valid_0's rmse: 43.0691
[49852]	valid_0's rmse: 43.0691
[49853]	valid_0's rmse: 43.0691
[49854]	valid_0's rmse: 43.0692
[49855]	valid_0's rmse: 43.0692
[49856]	valid_0's rmse: 43.0692
[49857]	valid_0's rmse: 43.0692
[49858]	

In [81]:
print('Save model...')
# save model to file
gbm.save_model('modelx.txt')#+id 55.43413937629549#55.7875
# gbm = lgb.Booster(model_file='model.txt') 
print('Start predicting...')
# predict
y_pred = gbm.predict(X_tes, num_iteration=gbm.best_iteration)
# eval
from sklearn.metrics import mean_squared_error
print('The rmse of prediction is:', mean_squared_error(y_tes, y_pred) ** 0.5)

Save model...
Start predicting...
The rmse of prediction is: 43.06784805356713


In [79]:
with open('./data/test4-id2.txt', 'rb') as data_file:
    line = pickle.load(data_file)
    line = zuhe(line)
col1 = [c for c in line if
       c not in ['TERMINALNO', 'O_LINENO', 'O_UP', 'Source_Station', 'Target_Station', 'O_TIME', 'aver_v', 'max_v',
                 'Diff_Time','Distance1', 'distance2']]
test = line[col1].values
y_pred = gbm.predict(test, num_iteration=gbm.best_iteration)

ValueError: could not convert string to float: '872-12425'

In [80]:
feim = pd.Series(gbm.feature_importance(),index=col)
feim = feim.sort_values(ascending=False)
feim

['ID', 'Distance', 'hour', 'is_peek', 'weekday', 'is_workday', 'dws', 'nws', 'dts', 'nts', 'is_rain', 'h_aver_diff', 'h_aver_d', 'h_aver_v', 'hour_weekday'] ['ID', 'Distance', 'hour', 'is_peek', 'weekday', 'is_workday', 'dws', 'nws', 'dts', 'nts', 'is_rain', 'h_aver_diff', 'h_aver_d', 'h_aver_v', 'hour_weekday']


In [72]:
line['pred'] = y_pred
sub1 = line[['O_LINENO','TERMINALNO', 'O_UP','Source_Station','Target_Station','O_TIME','pred']]
sub1.columns = ['LINE','TERMINALNO','UP','pred_start_stop_ID','pred_end_stop_ID','realTime','pred']
sub1 = sub1.reset_index()
del sub1['index']

sub=pd.read_csv("./toBePredicted_0605_segment.csv", sep=",")
sub['realTime'] = pd.to_datetime(sub['realTime'],format='%Y-%m-%d %H:%M:%S')
sub2 = sub[['LINE','TERMINALNO','UP','pred_start_stop_ID','pred_end_stop_ID','realTime']]
sub2=pd.merge(sub2,sub1,on=['LINE','TERMINALNO','UP','pred_start_stop_ID','pred_end_stop_ID','realTime'],how='left')
sub2
sub2.to_csv('./toBePredicted_0607_result.csv',sep=",",index=False)#0605 29.2467

print('finished')

finished


In [76]:
y_pred.mean()

413.2838735396812

In [152]:
X_tes_pred = gbm.predict(X_tes, num_iteration=gbm.best_iteration)
# eval
from sklearn.metrics import mean_squared_error
print('The rmse of prediction is:', mean_squared_error(y_tes, X_tes_pred) ** 0.5)
X_tes_pred.mean()

The rmse of prediction is: 55.43413937629549


141.97263876213552

In [70]:
day = '16'
train = pd.read_csv("/home/b418-xiwei/xzl/notebook/DC/data/train201710"+day+".csv", sep=",")
train['O_TIME'] = pd.to_datetime('2017-10-'+day+' '+train['O_TIME'],format='%Y-%m-%d %H:%M:%S')
train = train.groupby(['O_LINENO', 'O_TERMINALNO']).apply(lambda x:x.sort_values(by='O_TIME', ascending=True))
train = train[(train['O_LINENO']==55010)]
train

O_LINENO  O_TERMINALNO              O_TIME  \
O_LINENO O_TERMINALNO                                                        
55010    902450       21985778     55010        902450 2017-10-16 07:01:40   
                      21984586     55010        902450 2017-10-16 07:01:50   
                      21984414     55010        902450 2017-10-16 07:02:00   
                      21987391     55010        902450 2017-10-16 07:02:10   
                      21990547     55010        902450 2017-10-16 07:02:19   
                      21989321     55010        902450 2017-10-16 07:02:32   
                      21990029     55010        902450 2017-10-16 07:02:42   
                      21993297     55010        902450 2017-10-16 07:02:52   
                      21992951     55010        902450 2017-10-16 07:03:01   
                      21992776     55010        902450 2017-10-16 07:03:11   
                      21993041     55010        902450 2017-10-16 07:03:20   
                      21992044     55010        902450 2017-10-16 07:03:32   
                      21995869     55010        902450 2017-10-16 07:03:42   
                      21994447     55010        902450 2017-10-16 07:03:52   
                      21995334     55010        902450 2017-10-16 07:04:02   
                      21995003     55010        902450 2017-10-16 07:04:12   
                      21998285     55010        902450 2017-10-16 07:04:22   
                      21998123     55010        902450 2017-10-16 07:04:32   
                      21997995     55010        902450 2017-10-16 07:04:42   
                      21997822     55010        902450 2017-10-16 07:04:52   
                      22000785     55010        902450 2017-10-16 07:05:02   
                      22000409     55010        902450 2017-10-16 07:05:12   
                      22002518     55010        902450 2017-10-16 07:05:22   
                      22003423     55010        902450 2017-10-16 07:05:32   
                      22006884     55010        902450 2017-10-16 07:05:42   
                      22006554     55010        902450 2017-10-16 07:05:52   
                      22006388     55010        902450 2017-10-16 07:06:02   
                      22006425     55010        902450 2017-10-16 07:06:12   
                      22009403     55010        902450 2017-10-16 07:06:22   
                      22009077     55010        902450 2017-10-16 07:06:32   
...                                  ...           ...                 ...   
         907334       25273034     55010        907334 2017-10-16 18:03:56   
                      25284814     55010        907334 2017-10-16 18:04:06   
                      25285655     55010        907334 2017-10-16 18:04:16   
                      25284895     55010        907334 2017-10-16 18:04:26   
                      25284134     55010        907334 2017-10-16 18:04:36   
                      25284977     55010        907334 2017-10-16 18:04:46   
                      25273343     55010        907334 2017-10-16 18:04:56   
                      25284267     55010        907334 2017-10-16 18:05:06   
                      25284317     55010        907334 2017-10-16 18:05:16   
                      25283548     55010        907334 2017-10-16 18:05:26   
                      25284402     55010        907334 2017-10-16 18:05:36   
                      25284459     55010        907334 2017-10-16 18:05:46   
                      25281193     55010        907334 2017-10-16 18:05:56   
                      25273649     55010        907334 2017-10-16 18:06:06   
                      25275389     55010        907334 2017-10-16 18:06:16   
                      25298771     55010        907334 2017-10-16 18:06:26   
                      25298813     55010        907334 2017-10-16 18:06:36   
                      25298039     55010        907334 2017-10-16 18:06:46   
                      25286381     55010        907334

In [76]:
bus = train[(train['O_TIME']>'2017-10-16 07:02:00')&(train['O_TIME']<'2017-10-16 07:05:00')]
# # get_last_station(bus)
bus
# 

O_LINENO  O_TERMINALNO              O_TIME  \
O_LINENO O_TERMINALNO                                                        
55010    902450       21987391     55010        902450 2017-10-16 07:02:10   
                      21990547     55010        902450 2017-10-16 07:02:19   
                      21989321     55010        902450 2017-10-16 07:02:32   
                      21990029     55010        902450 2017-10-16 07:02:42   
                      21993297     55010        902450 2017-10-16 07:02:52   
                      21992951     55010        902450 2017-10-16 07:03:01   
                      21992776     55010        902450 2017-10-16 07:03:11   
                      21993041     55010        902450 2017-10-16 07:03:20   
                      21992044     55010        902450 2017-10-16 07:03:32   
                      21995869     55010        902450 2017-10-16 07:03:42   
                      21994447     55010        902450 2017-10-16 07:03:52   
                      21995334     55010        902450 2017-10-16 07:04:02   
                      21995003     55010        902450 2017-10-16 07:04:12   
                      21998285     55010        902450 2017-10-16 07:04:22   
                      21998123     55010        902450 2017-10-16 07:04:32   
                      21997995     55010        902450 2017-10-16 07:04:42   
                      21997822     55010        902450 2017-10-16 07:04:52   
         904361       21985481     55010        904361 2017-10-16 07:02:08   
                      21987701     55010        904361 2017-10-16 07:02:18   
                      21987702     55010        904361 2017-10-16 07:02:28   
                      21988759     55010        904361 2017-10-16 07:02:38   
                      21988415     55010        904361 2017-10-16 07:02:48   
                      21991682     55010        904361 2017-10-16 07:02:58   
                      21991348     55010        904361 2017-10-16 07:03:08   
                      21991389     55010        904361 2017-10-16 07:03:18   
                      21991216     55010        904361 2017-10-16 07:03:28   
                      21994183     55010        904361 2017-10-16 07:03:38   
                      21993820     55010        904361 2017-10-16 07:03:48   
                      21995917     55010        904361 2017-10-16 07:03:58   
                      21996620     55010        904361 2017-10-16 07:04:08   
...                                  ...           ...                 ...   
         904373       21991932     55010        904373 2017-10-16 07:03:07   
                      21991799     55010        904373 2017-10-16 07:03:17   
                      21991616     55010        904373 2017-10-16 07:03:27   
                      21994643     55010        904373 2017-10-16 07:03:37   
                      21996542     55010        904373 2017-10-16 07:03:47   
                      21994080     55010        904373 2017-10-16 07:03:57   
                      21993927     55010        904373 2017-10-16 07:04:07   
                      22000334     55010        904373 2017-10-16 07:04:17   
                      22000159     55010        904373 2017-10-16 07:04:27   
                      21999997     55010        904373 2017-10-16 07:04:37   
                      22000031     55010        904373 2017-10-16 07:04:47   
                      22003020     55010        904373 2017-10-16 07:04:57   
         907334       21984823     55010        907334 2017-10-16 07:02:07   
                      21989049     55010        907334 2017-10-16 07:02:17   
                      21988474     55010        907334 2017-10-16 07:02:27   
                      21988541     55010        907334 2017-10-16 07:02:37   
                      21988393     55010        907334 2017-10-16 07:02:47   
                      21991683     55010        907334 2017-10-16 07:02:57   
                      21991302     55010        907334

In [180]:
x = line['Diff_Time'] - line['h_aver_diff']
sum(x) / line.shape[0]

3.6263599551047894

In [182]:
sub=pd.read_csv("./toBePredicted_0603_result2.csv", sep=",")

In [69]:
# sum(sub['pred'] - sub['h_aver_diff']) / sub.shape[0]

In [43]:
def read_station_loc(line, on, start):
    path = './station/' + str(line) + '.txt'
    if os.path.exists(path):
        bus1 = pd.read_table(path, header=None, sep=',', encoding='utf-8')
        bus1.columns = ["O_UP", "Source_Station", "O_LATITUDE", "O_LONGITUDE"]
        b = bus1[(bus1['O_UP'] == on) & (bus1['Source_Station'] == start)]
        if b.shape[0] > 0:
            return str([b.iloc[0]['O_LATITUDE'],b.iloc[0]['O_LONGITUDE']])
        else:
            return str([-1,-1])
    else:
        return str([-1,-1])

In [37]:
read_station_loc(909, 1, 22)

[39.15202000000001, 117.1044]

In [45]:
with open('./data/test5-id.txt', 'rb') as data_file:
    test = pickle.load(data_file)

In [58]:
x = test[(test['Distance']==-1)&(test['h_aver_diff']==-1)] #Distance new_dist 440 #h_aver_diff 系列 1296
#test[(test['Distance']==-1)&(test['h_aver_diff']==-1)] 543
x = x.groupby(['O_LINENO','O_UP','Source_Station','Target_Station']).apply(lambda x:x.sort_values(by='O_TIME', ascending=True))
print(x['O_LINENO'].drop_duplicates())
x
# test1 = test[:5]
# test1.apply(lambda x: read_station_loc(x['O_LINENO'], x['O_UP'], x['Source_Station']),axis=1)

O_LINENO  O_UP  Source_Station  Target_Station        
572       0     25              26              365807      572
605       0     44              45              341756      605
55008     0     34              35              332885    55008
55009     0     13              14              391564    55009
55010     0     22              23              389366    55010
55012     0     13              14              357668    55012
55013     0     16              17              56103     55013
55014     0     15              16              236445    55014
55015     1     10              11              361431    55015
55051     0     23              24              93436     55051
55052     1     25              26              7162      55052
Name: O_LINENO, dtype: int64


ID  O_LINENO  \
O_LINENO O_UP Source_Station Target_Station                                
572      0    25             26             365807    57202526       572   
              26             27             365808    57202627       572   
              27             28             365809    57202728       572   
              28             29             365810    57202829       572   
              29             30             365811    57202930       572   
605      0    44             45             341756    60504445       605   
                                            438023    60504445       605   
                                            166954    60504445       605   
                                            215827    60504445       605   
              45             46             341757    60504546       605   
                                            438024    60504546       605   
                                            166955    60504546       605   
                                            215828    60504546       605   
              46             47             341758    60504647       605   
                                            166956    60504647       605   
                                            215829    60504647       605   
55008    0    34             35             332885  5500803435     55008   
                                            410712  5500803435     55008   
                                            263128  5500803435     55008   
                                            293267  5500803435     55008   
                                            296089  5500803435     55008   
              35             36             332886  5500803536     55008   
                                            410713  5500803536     55008   
                                            263129  5500803536     55008   
                                            293268  5500803536     55008   
                                            296090  5500803536     55008   
              36             37             332887  5500803637     55008   
                                            410714  5500803637     55008   
                                            263130  5500803637     55008   
                                            293269  5500803637     55008   
...                                                        ...       ...   
55051    1    41             42             213213  5505114142     55051   
                                            477094  5505114142     55051   
                                            360995  5505114142     55051   
              42             43             159456  5505114243     55051   
                                            23107   5505114243     55051   
                                            369293  5505114243     55051   
                                            213214  5505114243     55051   
                                            477095  5505114243     55051   
                                            360996  5505114243     55051   
              43             44             159457  5505114344     55051   
                                            23108   5505114344     55051   
                                            369294  5505114344     55051   
                                            213215  5505114344     55051   
                                            477096  5505114344     55051   
                                            360997  5505114344     55051   
55052    1    25             26             7162    5505212526     55052   
              26             27             7163    5505212627     55052   
              27             28             7164    5505212728     55052   
              28             29             7165    5505212829     55052   
              29             30             7166    5505212930     55052   
              30             31 

In [62]:
myresult = pd.read_csv("./toBePredicted_0608_result.csv", sep=",")
myresult[(myresult['LINE']==55008)]

LINE  TERMINALNO  UP  pred_start_stop_ID  pred_end_stop_ID  \
87068   55008      901542   0                  14                15   
87069   55008      901542   0                  15                16   
87070   55008      901542   0                  16                17   
87071   55008      901542   0                  17                18   
87072   55008      901542   0                  18                19   
87073   55008      901542   0                  19                20   
87074   55008      901542   0                  20                21   
87075   55008      901542   0                  21                22   
87076   55008      901542   0                  22                23   
87077   55008      901542   0                  23                24   
163916  55008      901542   0                  14                15   
163917  55008      901542   0                  15                16   
163918  55008      901542   0                  16                17   
163919  55008      901542   0                  17                18   
163920  55008      901542   0                  18                19   
163921  55008      901542   0                  19                20   
163922  55008      901542   0                  20                21   
163923  55008      901542   0                  21                22   
163924  55008      901542   0                  22                23   
163925  55008      901542   0                  23                24   
263113  55008      902311   0                  19                20   
263114  55008      902311   0                  20                21   
263115  55008      902311   0                  21                22   
263116  55008      902311   0                  22                23   
263117  55008      902311   0                  23                24   
263118  55008      902311   0                  24                25   
263119  55008      902311   0                  25                26   
263120  55008      902311   0                  26                27   
263121  55008      902311   0                  27                28   
263122  55008      902311   0                  28                29   
...       ...         ...  ..                 ...               ...   
410515  55008      902283   0                  21                22   
410516  55008      902283   0                  22                23   
410517  55008      902283   0                  23                24   
410689  55008      902283   0                  11                12   
410690  55008      902283   0                  12                13   
410691  55008      902283   0                  13                14   
410692  55008      902283   0                  14                15   
410693  55008      902283   0                  15                16   
410694  55008      902283   0                  16                17   
410695  55008      902283   0                  17                18   
410696  55008      902283   0                  18                19   
410697  55008      902283   0                  19                20   
410698  55008      902283   0                  20                21   
410699  55008      902283   0                  21                22   
410700  55008      902283   0                  22                23   
410701  55008      902283   0                  23                24   
410702  55008      902283   0                  24                25   
410703  55008      902283   0                  25                26   
410704  55008      902283   0                  26                27   
410705  55008      902283   0                  27                28   
410706  55008      902283   0                  28                29   
410707  55008      902283   0                  29                30   
410708  55008      902283   0                  30                31   
410709  55008      902283   0                  31                32   
410710  55008      902283   0    

In [122]:
test2 = pd.read_csv("./test5_id_with_segment_loc_crowd.csv", sep=",")
test2

Unnamed: 0        ID  O_LINENO  O_UP  Source_Station  Target_Station  \
0              209  86600809       866     0               8               9   
1              210  86600910       866     0               9              10   
2              211  86601011       866     0              10              11   
3              212  86601112       866     0              11              12   
4              213  86601213       866     0              12              13   
5              214  86601314       866     0              13              14   
6              215  86601415       866     0              14              15   
7              216  86601516       866     0              15              16   
8              217  86601617       866     0              16              17   
9              218  86601718       866     0              17              18   
10             219  86601819       866     0              18              19   
11             220  86601920       866     0              19              20   
12             221  86602021       866     0              20              21   
13             222  86602122       866     0              21              22   
14             223  86602223       866     0              22              23   
15             224  86602324       866     0              23              24   
16             225  86602425       866     0              24              25   
17             226  86602526       866     0              25              26   
18             227  86602627       866     0              26              27   
19             228  86602728       866     0              27              28   
20             229  86602829       866     0              28              29   
21             230  86602930       866     0              29              30   
22             231  86603031       866     0              30              31   
23             232  86603132       866     0              31              32   
24             233  86603233       866     0              32              33   
25             234  86603334       866     0              33              34   
26             235  86603435       866     0              34              35   
27             247  67313637       673     1              36              37   
28             248  67313738       673     1              37              38   
29             249  67313839       673     1              38              39   
...            ...       ...       ...   ...             ...             ...   
490350      490041  80400203       804     0               2               3   
490351      490042  80400304       804     0               3               4   
490352      490043  80400405       804     0               4               5   
490353      490044  80400506       804     0               5               6   
490354      490045  80400607       804     0               6               7   
490355      490046  80400708       804     0               7               8   
490356      490047  80400809       804     0               8               9   
490357      490048  80400910       804     0               9              10   
490358      490049  80401011       804     0              10              11   
490359      490050  80401112       804     0              11              12   
490360      490051  80401213       804     0              12              13   
490361      490052  80401314       804     0              13              14   
490362      490053  80401415       804     0              14              15   
490363      490054  80401516       804     0              15              16   
490364      490055  80401617       804     0              16              17   
490365      490056  80401718       804     0              17              18   
490366      490057  80401819       804     0              18              19   
490367      490058  80401920       804     0              19              20   
490368  

In [193]:
train2 = pd.read_csv("./train_id_loc_with_crowd.csv", sep=",")
train2

/home/b418-xiwei/anaconda3/envs/dl/lib/python3.6/site-packages/tqdm/_monitor.py:89: TqdmSynchronisationWarning: Set changed size during iteration (see https://github.com/tqdm/tqdm/issues/481)
  TqdmSynchronisationWarning)


Unnamed: 0          ID  O_LINENO  O_UP  Source_Station  \
0                  1    80412021       804     1              20   
1                  2    80412122       804     1              21   
2                  3    80412223       804     1              22   
3                  4    80412324       804     1              23   
4                  5    80412425       804     1              24   
5                  6    80400203       804     0               2   
6                  7    80400304       804     0               3   
7                  8    80400405       804     0               4   
8                  9    80400506       804     0               5   
9                 10    80400607       804     0               6   
10                11    80400708       804     0               7   
11                12    80400809       804     0               8   
12                13    80400910       804     0               9   
13                14    80401011       804     0              10   
14                15    80401112       804     0              11   
15                16    80401213       804     0              12   
16                17    80401314       804     0              13   
17                18    80401415       804     0              14   
18                19    80401516       804     0              15   
19                20    80401617       804     0              16   
20                21    80401718       804     0              17   
21                22    80401819       804     0              18   
22                23    80401920       804     0              19   
23                24    80402021       804     0              20   
24                25    80402122       804     0              21   
25                26    80402223       804     0              22   
26                28    80410203       804     1               2   
27                29    80410304       804     1               3   
28                30    80410405       804     1               4   
29                31    80410506       804     1               5   
...              ...         ...       ...   ...             ...   
13963716          10  5501200304     55012     0               3   
13963717          11  5501200405     55012     0               4   
13963718          12  5501200506     55012     0               5   
13963719          13  5501200607     55012     0               6   
13963720          14  5501200708     55012     0               7   
13963721          15  5501200809     55012     0               8   
13963722          17  5501210405     55012     1               4   
13963723          18  5501210506     55012     1               5   
13963724          19  5501210607     55012     1               6   
13963725          20  5501210708     55012     1               7   
13963726          21  5501210809     55012     1               8   
13963727          23  5501200203     55012     0               2   
13963728          24  5501200304     55012     0               3   
13963729          25  5501200405     55012     0               4   
13963730          26  5501200506     55012     0               5   
13963731          27  5501200607     55012     0               6   
13963732          28  5501200708     55012     0               7   
13963733          29  5501200809     55012     0               8   
13963734           1  5500910203     55009     1               2   
13963735           2  5500910304     55009     1               3   
13963736           3  5500910405     55009     1               4   
13963737           4  5500910506     55009     1               5   
13963738           6  5500900203     55009     0               2   
13963739           7  5500900304     55009     0               3   
13963740           8  5500900405     55009     0               4   
13963741           9  5500900506     55009     0               5   
13963742          11  5500910203     55009     1               2  

In [81]:
#['new_ID'] ['Distance', 'hour', 'is_peek', 'weekday', 'is_workday', 'dws', 'nws', 
#'dts', 'nts', 'is_rain', 'h_aver_diff', 'h_aver_d', 'h_aver_v', 'hour_weekday', 'peak_workday']
def zuhe(line):
    line['hour'] = line['hour'].astype(str)
    line['weekday'] = line['weekday'].astype(str)
    line['is_peek'] = line['is_peek'].astype(str)
    line['is_workday'] = line['is_workday'].astype(str)
                                   
    line['hour_weekday'] = line['hour'] + line['weekday']
    line['peak_workday'] = line['is_peek'] + line['is_workday']
    
    line['hour_weekday'] = line['hour_weekday'].astype(int)
    line['peak_workday'] = line['peak_workday'].astype(int)
    
    line['hour'] = line['hour'].astype(int)
    line['is_peek'] = line['is_peek'].astype(int)
    line['is_workday'] = line['is_workday'].astype(int)
    line['weekday'] = line['weekday'].astype(int)

    return line

In [194]:
print(train2['s_x'].max())#40.0777
print(train2['s_x'].min())#38.632540000000006


40.0777
38.632540000000006


In [195]:
print(train2['s_y'].max())#118.16
print(train2['s_y'].min())#116.9006

118.16
116.9006


/home/b418-xiwei/anaconda3/envs/dl/lib/python3.6/site-packages/tqdm/_monitor.py:89: TqdmSynchronisationWarning: Set changed size during iteration (see https://github.com/tqdm/tqdm/issues/481)
  TqdmSynchronisationWarning)


In [196]:
print(train2['e_x'].max())#40.0777
print(train2['e_x'].min())#38.632540000000006

40.0777
38.632540000000006


In [197]:
print(train2['e_y'].max())#117.979
print(train2['e_y'].min())#116.9006

117.979
116.9006


/home/b418-xiwei/anaconda3/envs/dl/lib/python3.6/site-packages/tqdm/_monitor.py:89: TqdmSynchronisationWarning: Set changed size during iteration (see https://github.com/tqdm/tqdm/issues/481)
  TqdmSynchronisationWarning)


In [98]:
a = test2['s_x'].as_matrix()
np.percentile(a,50)

/home/b418-xiwei/anaconda3/envs/dl/lib/python3.6/site-packages/numpy/lib/function_base.py:4291: RuntimeWarning: Invalid value encountered in percentile
  interpolation=interpolation)


nan

In [198]:
#划分格子并获取格子编号
import math
max_x = 40.0777#max(test2['s_x'].max(),test2['e_x'].max()) + 0.00001
min_x = 38.6325#min(test2['s_x'].min(),test2['e_x'].min())
max_y = 118.16#max(test2['s_y'].max(),test2['e_y'].max()) + 0.00001
min_y = 116.900#min(test2['s_y'].min(),test2['e_y'].min())
lx = (max_x - min_x) / 50
ly = (max_y - min_y) / 33
print(min_x,max_x)
print(min_y,max_y)
print(lx,ly)
def get_ij(x,y):
#     print(x,y)
    i = math.floor((x - min_x)/lx)
    j = math.floor((y - min_y)/ly)
    num = i*33+(j+1)
    return num
train2['s_ij'] = train2.progress_apply(lambda x:get_ij(x['s_x'],x['s_y']) if (np.all(pd.notnull(x['s_x'])) and np.all(pd.notnull(x['s_y']))) else -1,axis=1)
train2['e_ij'] = train2.progress_apply(lambda x:get_ij(x['e_x'],x['e_y']) if (np.all(pd.notnull(x['e_x'])) and np.all(pd.notnull(x['e_y']))) else -1,axis=1)
train2



  0%|          | 0/13963746 [00:00<?, ?it/s]

38.6325 40.0777
116.9 118.16
0.028903999999999996 0.03818181818181791


/home/b418-xiwei/anaconda3/envs/dl/lib/python3.6/site-packages/tqdm/_monitor.py:89: TqdmSynchronisationWarning: Set changed size during iteration (see https://github.com/tqdm/tqdm/issues/481)
  TqdmSynchronisationWarning)


  0%|          | 1/13963746 [00:49<190503:38:49, 49.11s/it]

  0%|          | 2/13963746 [00:49<133654:57:51, 34.46s/it]

  0%|          | 1058/13963746 [00:49<93551:30:35, 24.12s/it]

  0%|          | 2100/13963746 [00:49<65481:16:53, 16.88s/it]

  0%|          | 3171/13963746 [00:49<45833:29:23, 11.82s/it]

  0%|          | 4192/13963746 [00:49<32081:12:37,  8.27s/it]

  0%|          | 5258/13963746 [00:49<22455:14:29,  5.79s/it]

  0%|          | 6338/13963746 [00:49<15717:33:38,  4.05s/it]

  0%|          | 7424/13963746 [00:50<11001:32:36,  2.84s/it]

  0%|          | 8509/13963746 [00:50<7700:35:20,  1.99s/it] 

  0%|          | 9649/13963746 [00:50<5390:04:26,  1.39s/it]

  0%|          | 10848/13963746 [00:50<3772:49:28,  1.03it/s]

  0%|          | 12050/13

  2%|▏         | 254644/13963746 [01:13<25:02, 9123.14it/s]

  2%|▏         | 255570/13963746 [01:14<25:36, 8918.90it/s]

  2%|▏         | 256473/13963746 [01:14<26:00, 8781.10it/s]

  2%|▏         | 257359/13963746 [01:14<26:33, 8599.37it/s]

  2%|▏         | 258325/13963746 [01:14<25:41, 8892.17it/s]

  2%|▏         | 259410/13963746 [01:14<24:17, 9400.75it/s]

  2%|▏         | 260498/13963746 [01:14<23:18, 9798.36it/s]

  2%|▏         | 261529/13963746 [01:14<22:57, 9945.00it/s]

  2%|▏         | 262643/13963746 [01:14<22:13, 10273.95it/s]

  2%|▏         | 263680/13963746 [01:14<22:22, 10206.32it/s]

  2%|▏         | 264708/13963746 [01:14<22:45, 10029.82it/s]

  2%|▏         | 265730/13963746 [01:15<22:38, 10083.49it/s]

  2%|▏         | 266820/13963746 [01:15<22:07, 10314.85it/s]

  2%|▏         | 267939/13963746 [01:15<21:36, 10560.30it/s]

  2%|▏         | 269019/13963746 [01:15<21:28, 10628.44it/s]

  2%|▏         | 270085/13963746 [01:15<21:43, 10505.92it/s]

  2%|▏         |

  4%|▎         | 511004/13963746 [01:39<23:46, 9428.63it/s]

  4%|▎         | 512076/13963746 [01:39<22:55, 9781.87it/s]

  4%|▎         | 513094/13963746 [01:39<22:38, 9897.88it/s]

  4%|▎         | 514113/13963746 [01:39<22:27, 9983.05it/s]

  4%|▎         | 515132/13963746 [01:39<22:19, 10041.54it/s]

  4%|▎         | 516149/13963746 [01:39<22:14, 10077.25it/s]

  4%|▎         | 517165/13963746 [01:39<22:11, 10100.58it/s]

  4%|▎         | 518222/13963746 [01:39<21:53, 10236.13it/s]

  4%|▎         | 519248/13963746 [01:39<21:55, 10221.09it/s]

  4%|▎         | 520307/13963746 [01:39<21:41, 10328.03it/s]

  4%|▎         | 521527/13963746 [01:40<20:41, 10825.39it/s]

  4%|▎         | 522617/13963746 [01:40<20:48, 10763.22it/s]

  4%|▍         | 523699/13963746 [01:40<20:50, 10747.02it/s]

  4%|▍         | 524790/13963746 [01:40<20:45, 10793.11it/s]

  4%|▍         | 525881/13963746 [01:40<20:41, 10827.01it/s]

  4%|▍         | 526966/13963746 [01:40<20:55, 10699.52it/s]

  4%|▍      

...

 94%|█████████▍| 13134132/13963746 [23:16<01:19, 10418.35it/s]

 94%|█████████▍| 13135194/13963746 [23:16<01:19, 10478.01it/s]

 94%|█████████▍| 13136272/13963746 [23:17<01:18, 10565.13it/s]

 94%|█████████▍| 13137330/13963746 [23:17<01:18, 10482.28it/s]

 94%|█████████▍| 13138425/13963746 [23:17<01:17, 10616.22it/s]

 94%|█████████▍| 13139488/13963746 [23:17<01:18, 10446.87it/s]

 94%|█████████▍| 13140535/13963746 [23:17<01:22, 10011.47it/s]

 94%|█████████▍| 13141542/13963746 [23:17<01:23, 9843.07it/s] 

 94%|█████████▍| 13142531/13963746 [23:17<01:24, 9765.96it/s]

 94%|█████████▍| 13143511/13963746 [23:17<01:24, 9688.34it/s]

 94%|█████████▍| 13144483/13963746 [23:17<01:24, 9666.44it/s]

 94%|█████████▍| 13145452/13963746 [23:17<01:26, 9511.49it/s]

 94%|█████████▍| 13146409/13963746 [23:18<01:25, 9526.59it/s]

 94%|█████████▍| 13147366/13963746 [23:18<01:25, 9537.66it/s]

 94%|█████████▍| 13148321/13963746 [23:18<01:25, 9494.81it/s]

 94%|█████████▍| 13149280/13963746 [23:18<01:25

 96%|█████████▌| 13367716/13963746 [23:40<00:56, 10538.75it/s]

 96%|█████████▌| 13368771/13963746 [23:41<00:57, 10398.96it/s]

 96%|█████████▌| 13369812/13963746 [23:41<01:01, 9698.83it/s] 

 96%|█████████▌| 13370799/13963746 [23:41<01:00, 9748.35it/s]

 96%|█████████▌| 13371781/13963746 [23:41<01:05, 9024.87it/s]

 96%|█████████▌| 13372700/13963746 [23:41<01:05, 9033.14it/s]

 96%|█████████▌| 13373668/13963746 [23:41<01:04, 9216.40it/s]

 96%|█████████▌| 13374615/13963746 [23:41<01:03, 9287.72it/s]

 96%|█████████▌| 13375639/13963746 [23:41<01:01, 9552.77it/s]

 96%|█████████▌| 13376601/13963746 [23:41<01:04, 9044.51it/s]

 96%|█████████▌| 13377516/13963746 [23:41<01:06, 8810.96it/s]

 96%|█████████▌| 13378406/13963746 [23:42<01:12, 8120.65it/s]

 96%|█████████▌| 13379302/13963746 [23:42<01:09, 8353.81it/s]

 96%|█████████▌| 13380336/13963746 [23:42<01:05, 8863.75it/s]

 96%|█████████▌| 13381370/13963746 [23:42<01:02, 9260.19it/s]

 96%|█████████▌| 13382386/13963746 [23:42<01:01, 951

 97%|█████████▋| 13610004/13963746 [24:05<00:34, 10190.46it/s]

 97%|█████████▋| 13611030/13963746 [24:05<00:34, 10161.66it/s]

 97%|█████████▋| 13612051/13963746 [24:05<00:35, 9939.20it/s] 

 97%|█████████▋| 13613050/13963746 [24:05<00:35, 9893.42it/s]

 97%|█████████▋| 13614043/13963746 [24:05<00:35, 9777.03it/s]

 98%|█████████▊| 13615299/13963746 [24:05<00:33, 10471.67it/s]

 98%|█████████▊| 13616362/13963746 [24:05<00:34, 9989.13it/s] 

 98%|█████████▊| 13617377/13963746 [24:05<00:34, 9909.97it/s]

 98%|█████████▊| 13618383/13963746 [24:05<00:34, 9953.28it/s]

 98%|█████████▊| 13619416/13963746 [24:06<00:34, 10062.65it/s]

 98%|█████████▊| 13620428/13963746 [24:06<00:35, 9589.90it/s] 

 98%|█████████▊| 13621493/13963746 [24:06<00:34, 9883.83it/s]

 98%|█████████▊| 13622575/13963746 [24:06<00:33, 10145.73it/s]

 98%|█████████▊| 13623598/13963746 [24:06<00:33, 10143.75it/s]

 98%|█████████▊| 13624662/13963746 [24:06<00:32, 10285.41it/s]

 98%|█████████▊| 13625695/13963746 [24:06<00:

 99%|█████████▉| 13854014/13963746 [24:29<00:11, 9356.98it/s] 

 99%|█████████▉| 13855057/13963746 [24:29<00:11, 9654.52it/s]

 99%|█████████▉| 13856083/13963746 [24:29<00:10, 9826.28it/s]

 99%|█████████▉| 13857126/13963746 [24:29<00:10, 9998.58it/s]

 99%|█████████▉| 13858163/13963746 [24:29<00:10, 10065.76it/s]

 99%|█████████▉| 13859218/13963746 [24:29<00:10, 10204.49it/s]

 99%|█████████▉| 13860284/13963746 [24:30<00:10, 10336.85it/s]

 99%|█████████▉| 13861323/13963746 [24:30<00:09, 10305.69it/s]

 99%|█████████▉| 13862361/13963746 [24:30<00:09, 10325.73it/s]

 99%|█████████▉| 13863420/13963746 [24:30<00:09, 10402.36it/s]

 99%|█████████▉| 13864462/13963746 [24:30<00:09, 10368.21it/s]

 99%|█████████▉| 13865522/13963746 [24:30<00:09, 10434.35it/s]

 99%|█████████▉| 13866584/13963746 [24:30<00:09, 10397.21it/s]

 99%|█████████▉| 13867625/13963746 [24:30<00:09, 9978.66it/s] 

 99%|█████████▉| 13868654/13963746 [24:30<00:09, 10065.80it/s]

 99%|█████████▉| 13869781/13963746 [24:30<0

Unnamed: 0          ID  O_LINENO  O_UP  Source_Station  \
0                  1    80412021       804     1              20   
1                  2    80412122       804     1              21   
2                  3    80412223       804     1              22   
3                  4    80412324       804     1              23   
4                  5    80412425       804     1              24   
5                  6    80400203       804     0               2   
6                  7    80400304       804     0               3   
7                  8    80400405       804     0               4   
8                  9    80400506       804     0               5   
9                 10    80400607       804     0               6   
10                11    80400708       804     0               7   
11                12    80400809       804     0               8   
12                13    80400910       804     0               9   
13                14    80401011       804     0              10   
14                15    80401112       804     0              11   
15                16    80401213       804     0              12   
16                17    80401314       804     0              13   
17                18    80401415       804     0              14   
18                19    80401516       804     0              15   
19                20    80401617       804     0              16   
20                21    80401718       804     0              17   
21                22    80401819       804     0              18   
22                23    80401920       804     0              19   
23                24    80402021       804     0              20   
24                25    80402122       804     0              21   
25                26    80402223       804     0              22   
26                28    80410203       804     1               2   
27                29    80410304       804     1               3   
28                30    80410405       804     1               4   
29                31    80410506       804     1               5   
...              ...         ...       ...   ...             ...   
13963716          10  5501200304     55012     0               3   
13963717          11  5501200405     55012     0               4   
13963718          12  5501200506     55012     0               5   
13963719          13  5501200607     55012     0               6   
13963720          14  5501200708     55012     0               7   
13963721          15  5501200809     55012     0               8   
13963722          17  5501210405     55012     1               4   
13963723          18  5501210506     55012     1               5   
13963724          19  5501210607     55012     1               6   
13963725          20  5501210708     55012     1               7   
13963726          21  5501210809     55012     1               8   
13963727          23  5501200203     55012     0               2   
13963728          24  5501200304     55012     0               3   
13963729          25  5501200405     55012     0               4   
13963730          26  5501200506     55012     0               5   
13963731          27  5501200607     55012     0               6   
13963732          28  5501200708     55012     0               7   
13963733          29  5501200809     55012     0               8   
13963734           1  5500910203     55009     1               2   
13963735           2  5500910304     55009     1               3   
13963736           3  5500910405     55009     1               4   
13963737           4  5500910506     55009     1               5   
13963738           6  5500900203     55009     0               2   
13963739           7  5500900304     55009     0               3   
13963740           8  5500900405     55009     0               4   
13963741           9  5500900506     55009     0               5   
13963742          11  5500910203     55009     1               2  

In [200]:
with open('./data/train-id-crowd-grid.txt', 'wb') as data_file:
    pickle.dump(train2, data_file)

/home/b418-xiwei/anaconda3/envs/dl/lib/python3.6/site-packages/tqdm/_monitor.py:89: TqdmSynchronisationWarning: Set changed size during iteration (see https://github.com/tqdm/tqdm/issues/481)
  TqdmSynchronisationWarning)


In [156]:
%matplotlib inline 
test_5['s_ij'].value_counts()[:50]#.plot(kind='bar')#.quantile(.1)

472     44297
501     27933
444     26709
471     26273
443     22531
500     20829
502     20291
473     17923
414     17532
442     16837
529     14981
415     14324
474     12857
416     11968
445     11245
530     10350
528      7860
470      6862
557      6692
503      6550
332      5941
387      5471
499      5175
357      5011
413      4749
441      4720
446      4704
417      4080
388      3427
361      3093
531      2890
469      2811
412      2728
559      2506
605      2462
360      2461
1084     2361
586      2357
386      2347
418      2242
389      2162
385      2099
1406     2021
615      1752
729      1715
535      1652
558      1636
506      1588
189      1528
447      1525
Name: s_ij, dtype: int64

In [142]:
test_5[(test_5['s_ij']==-1)]

Unnamed: 0          ID  O_LINENO  O_UP  Source_Station  \
8632         56100  5501301314     55013     0              13   
8633         56101  5501301415     55013     0              14   
8634         56102  5501301516     55013     0              15   
8635         56103  5501301617     55013     0              16   
8636         56104  5501301718     55013     0              17   
8637         56105  5501301819     55013     0              18   
8638         56106  5501301920     55013     0              19   
8639         56107  5501302021     55013     0              20   
8640         56108  5501302122     55013     0              21   
8641         56109  5501302223     55013     0              22   
8642         56110  5501302324     55013     0              23   
8643         56111  5501302425     55013     0              24   
8644         56112  5501302526     55013     0              25   
8645         56113  5501302627     55013     0              26   
8646         56114  5501302728     55013     0              27   
8647         56115  5501302829     55013     0              28   
8648         56116  5501302930     55013     0              29   
8649         56117  5501303031     55013     0              30   
8650         56118  5501303132     55013     0              31   
8651         56119  5501303233     55013     0              32   
13242        89209  5501012526     55010     1              25   
13243        89210  5501012627     55010     1              26   
13244        89211  5501012728     55010     1              27   
13245        89212  5501012829     55010     1              28   
13246        89213  5501012930     55010     1              29   
13247        89214  5501013031     55010     1              30   
13248        89215  5501013132     55010     1              31   
13249        89216  5501013233     55010     1              32   
13250        89217  5501013334     55010     1              33   
13251        89218  5501013435     55010     1              34   
...            ...         ...       ...   ...             ...   
488486      477060  5505110708     55051     1               7   
488491      477065  5505111213     55051     1              12   
488493      477067  5505111415     55051     1              14   
488496      477070  5505111718     55051     1              17   
488497      477071  5505111819     55051     1              18   
488498      477072  5505111920     55051     1              19   
488499      477073  5505112021     55051     1              20   
488500      477074  5505112122     55051     1              21   
488501      477075  5505112223     55051     1              22   
488502      477076  5505112324     55051     1              23   
488503      477077  5505112425     55051     1              24   
488504      477078  5505112526     55051     1              25   
488505      477079  5505112627     55051     1              26   
488506      477080  5505112728     55051     1              27   
488507      477081  5505112829     55051     1              28   
488508      477082  5505112930     55051     1              29   
488509      477083  5505113031     55051     1              30   
488510      477084  5505113132     55051     1              31   
488511      477085  5505113233     55051     1              32   
488512      477086  5505113334     55051     1              33   
488513      477087  5505113435     55051     1              34   
488514      477088  5505113536     55051     1              35   
488515      477089  5505113637     55051     1              36   
488516      477090  5505113738     55051     1              37   
488517      477091  5505113839     55051     1              38   
488518      477092  5505113940     55051     1              39   
488519      477093  5505114041     55051     1              40   
488520      477094  5505114142     55051     1              41   
488521      477095  5505114243     55051     1  

In [187]:
with open('./history/1_0_0_0.txt', 'rb') as data_file:
    h = pickle.load(data_file).reset_index()
h['Line'] = 1
h

index  O_UP  Source_Station  Target_Station  Distance  Diff_Time  \
0          0     0               1               2  0.621531        341   
1          1     0               2               3  0.583005         45   
2          2     0               3               4  0.533489         64   
3          3     0               4               5  0.560464        113   
4          4     0               5               6  1.137853        154   
5          5     0               6               7  0.470693         62   
6          6     0               7               8  0.363559         33   
7          7     0               8               9  0.657603         74   
8          8     0               9              10  0.211337         90   
9          9     0              10              11  0.516312        133   
10        10     0              11              12  0.475580         90   
11        11     0              12              13  0.300321         40   
12        12     0              13              14  0.464933         52   
13        13     0              14              15  1.335214        185   
14        14     0              15              16  0.586234        121   
15        15     0              16              17  0.216303         39   
16        16     0              17              18  0.406526         70   
17        17     0              18              19  0.556968        151   
18        18     0              19              20  1.037118        130   
19        19     0              20              21  0.184317         39   
20        20     0              21              22  0.455232         44   
21        21     0              22              23  0.619070         94   
22        22     0              23              24  0.600119        121   
23        23     0              24              25  0.476415         29   
24        24     0              25              26  0.332997         36   
25        25     0              26              27  0.468843         71   
26        27     0              28              29  0.286119         21   
27        28     0              29              30  0.322967         71   
28        29     1               3               4  0.997548        480   
29        30     1               4               5  0.634857        110   
...      ...   ...             ...             ...       ...        ...   
11235   5788     0              26              27  0.556921         90   
11236   5789     0              27              28  0.580940         70   
11237   5790     0              28              29  0.296460         51   
11238   5791     0              29              30  0.321991         50   
11239   5792     1               3               4  0.691582        190   
11240   5793     1               4               5  0.582471         70   
11241   5794     1               5               6  0.373580         40   
11242   5795     1               6               7  0.462449         41   
11243   5796     1               7               8  0.358510         26   
11244   5797     1               8               9  0.360916         83   
11245   5798     1               9              10  0.738258        100   
11246   5799     1              10              11  0.446573         60   
11247   5800     1              11              12  0.434736         80   
11248   5801     1              12              13  0.872166        111   
11249   5802     1              13              14  0.334999        130   
11250   5803     1              14              15  0.585504        120   
11251   5804     1              15              16  0.175793         20   
11252   5805     1              16              17  0.615590        168   
11253   5806     1              17              18  1.439911        173   
11254   5807     1              18              19  0.370744         56   
11255   5808     1              19              20  0.380716         60   
11256   5809     1              

/home/b418-xiwei/anaconda3/envs/dl/lib/python3.6/site-packages/tqdm/_monitor.py:89: TqdmSynchronisationWarning: Set changed size during iteration (see https://github.com/tqdm/tqdm/issues/481)
  TqdmSynchronisationWarning)


In [160]:
#线路-站点编号与格子的对应关系
with open('./data/test-id-crowd-grid.txt', 'wb') as data_file:
    pickle.dump(test_5, data_file)


In [4]:
from tqdm import tqdm, tqdm_pandas
import math

tqdm.pandas()


def read_station_loc(line, on, start):
    path = './station/' + str(line) + '.txt'
    if os.path.exists(path):
        bus1 = pd.read_table(path, header=None, sep=',', encoding='utf-8')
        bus1.columns = ["O_UP", "Source_Station", "O_LATITUDE", "O_LONGITUDE"]
        b = bus1[(bus1['O_UP'] == on) & (bus1['Source_Station'] == start)]
        if b.shape[0] > 0:
            return str([b.iloc[0]['O_LATITUDE'], b.iloc[0]['O_LONGITUDE']])
        else:
            return str([-1, -1])
    else:
        return str([-1, -1])

#38.65936 40.07771
#116.917 117.97901
max_x = 40.0777#max(test2['s_x'].max(),test2['e_x'].max()) + 0.00001
min_x = 38.6325#min(test2['s_x'].min(),test2['e_x'].min())
max_y = 118.16#max(test2['s_y'].max(),test2['e_y'].max()) + 0.00001
min_y = 116.900#min(test2['s_y'].min(),test2['e_y'].min())
lx = (max_x - min_x) / 50
ly = (max_y - min_y) / 33
print(min_x, max_x)
print(min_y, max_y)
print(lx, ly)


def get_ij(x, y):
    i = math.floor((x - min_x) / lx)
    j = math.floor((y - min_y) / ly)
    num = i * 33 + (j + 1)
    return num


# progress_apply
def process(train_id):
    train_id['Source_loc'] = train_id.progress_apply(lambda x: read_station_loc(x['Line'], x['O_UP'], x['Source_Station']), axis=1)
    train_id['end_loc'] = train_id.progress_apply(lambda x: read_station_loc(x['Line'], x['O_UP'], x['Target_Station']), axis=1)
    train_id['s_x'] = train_id.Source_loc.apply(lambda x: x[1:-1].split(',')[0].replace(' ', ""))
    train_id['s_y'] = train_id.Source_loc.apply(lambda x: x[1:-1].split(',')[1].replace(' ', ""))
    train_id['e_x'] = train_id.end_loc.apply(lambda x: x[1:-1].split(',')[0].replace(' ', ""))
    train_id['e_y'] = train_id.end_loc.apply(lambda x: x[1:-1].split(',')[1].replace(' ', ""))

    train_id['s_x'] = train_id.s_x.str.extract('(\d+\.\d+)', expand=False)
    train_id['s_y'] = train_id.s_y.str.extract('(\d+\.\d+)', expand=False)
    train_id['e_x'] = train_id.e_x.str.extract('(\d+\.\d+)', expand=False)
    train_id['e_y'] = train_id.e_y.str.extract('(\d+\.\d+)', expand=False)

    train_id['s_x'] = train_id.s_x.astype(np.float32)
    train_id['s_y'] = train_id.s_y.astype(np.float32)
    train_id['e_x'] = train_id.e_x.astype(np.float32)
    train_id['e_y'] = train_id.e_y.astype(np.float32)

    train_id['s_ij'] = train_id.progress_apply(
        lambda x: get_ij(x['s_x'], x['s_y']) if (np.all(pd.notnull(x['s_x'])) and np.all(pd.notnull(x['s_y']))) else -1,
        axis=1)
    train_id['e_ij'] = train_id.progress_apply(
        lambda x: get_ij(x['e_x'], x['e_y']) if (np.all(pd.notnull(x['e_x'])) and np.all(pd.notnull(x['e_y']))) else -1,
        axis=1)
    del train_id['Source_loc'], train_id['end_loc']
    return train_id

38.6325 40.0777
116.9 118.16
0.028903999999999996 0.03818181818181791


In [5]:
hi = process(hi)
hi

  0%|          | 985/17301720 [00:09<23:58:23, 200.46it/s] /home/b418-xiwei/anaconda3/envs/dl/lib/python3.6/site-packages/tqdm/_monitor.py:89: TqdmSynchronisationWarning: Set changed size during iteration (see https://github.com/tqdm/tqdm/issues/481)
  TqdmSynchronisationWarning)
 56%|█████▋    | 9762126/17301720 [11:02:13<7:47:12, 268.96it/s] IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)

100%|██████████| 17301720/17301720 [29:28<00:00, 9785.07it/s] 


index  O_UP  Source_Station  Target_Station  Distance  Diff_Time  \
0       0     0               1               2  0.621531        341   
1       1     0               2               3  0.583005         45   
2       2     0               3               4  0.533489         64   
3       3     0               4               5  0.560464        113   
4       4     0               5               6  1.137853        154   
5       5     0               6               7  0.470693         62   
6       6     0               7               8  0.363559         33   
7       7     0               8               9  0.657603         74   
8       8     0               9              10  0.211337         90   
9       9     0              10              11  0.516312        133   
10     10     0              11              12  0.475580         90   
11     11     0              12              13  0.300321         40   
12     12     0              13              14  0.464933         52   
13     13     0              14              15  1.335214        185   
14     14     0              15              16  0.586234        121   
15     15     0              16              17  0.216303         39   
16     16     0              17              18  0.406526         70   
17     17     0              18              19  0.556968        151   
18     18     0              19              20  1.037118        130   
19     19     0              20              21  0.184317         39   
20     20     0              21              22  0.455232         44   
21     21     0              22              23  0.619070         94   
22     22     0              23              24  0.600119        121   
23     23     0              24              25  0.476415         29   
24     24     0              25              26  0.332997         36   
25     25     0              26              27  0.468843         71   
26     27     0              28              29  0.286119         21   
27     28     0              29              30  0.322967         71   
28     29     1               3               4  0.997548        480   
29     30     1               4               5  0.634857        110   
..    ...   ...             ...             ...       ...        ...   
42     56     0               5               6  0.515931         80   
43     57     0               6               7  0.757535         80   
44     58     0               7               8  1.022667        120   
45     59     1               1               2  0.597859        120   
46     11     0               6               7  0.750089         90   
47     12     0               7               8  1.013736        130   
48     13     1               1               2  0.619243        790   
49     14     1               2               3  0.947343        100   
50     15     1               3               4  0.756596         90   
51     16     1               4               5  0.444499         70   
52     17     1               5               6  0.856311        190   
53     18     1               6               7  1.281640        220   
54     19     1               7               8  0.474778         90   
55     20     0               3               4  2.385840        780   
56     21     0               4               5  0.598337        130   
57     22     0               5               6  0.531152        120   
58     23     0               6               7  0.708724         80   
59     24     0               7               8  1.062552        120   
60     25     1               1               2  0.530822        730   
61     26     1               2               3  1.018405        140   
62     27     1               3               4  0.794306         90   
63     28     1               4               5  0.441209        121   
64     29     1               5               6  0.755656        300   
65     30     1               6             

In [6]:
with open('./data/full_history_plus', 'wb') as data_file:
    pickle.dump(hi, data_file)

In [192]:
# history -> loc and grid
dir = "./history/"
history = pd.DataFrame()
for root, dirs, files in os.walk(dir):
    for file in tqdm(files):
        s = os.path.join(root,file)
        print (s)
        line = file.split('_')[0]
        with open(s, 'rb') as data_file:
            h = pickle.load(data_file).reset_index()
        h['Line'] = line
        h['is_rain'] = file.split('_')[1]
        h['is_workday'] = file.split('_')[2]
        h['is_peek'] = file.split('_')[3].split('.')[0]

        history = pd.concat([history,h])
with open('./data/full_history', 'wb') as data_file:
    pickle.dump(history, data_file)
print('finished')
#         h = process(line,h)
#         with open('./history2/'+file, 'wb') as data_file:
#             pickle.dump(h, data_file)



  0%|          | 0/3488 [00:00<?, ?it/s]

./history/1_0_0_0.txt
./history/1_0_0_1.txt
./history/1_0_1_0.txt
./history/1_0_1_1.txt
./history/1_1_0_0.txt




  0%|          | 5/3488 [00:00<02:40, 21.75it/s]

  0%|          | 7/3488 [00:00<02:58, 19.52it/s]

./history/1_1_0_1.txt
./history/1_1_1_0.txt
./history/1_1_1_1.txt




  0%|          | 8/3488 [00:00<03:33, 16.26it/s]

  0%|          | 10/3488 [00:00<03:28, 16.70it/s]

...

./history/334_1_0_1.txt




100%|█████████▉| 3487/3488 [1:59:01<00:02,  2.05s/it]

./history/334_1_1_1.txt




100%|██████████| 3488/3488 [1:59:03<00:00,  2.05s/it]



0it [00:00, ?it/s]



finished


In [3]:
with open('./data/full_history', 'rb') as data_file:
    hi = pickle.load(data_file)
hi

index  O_UP  Source_Station  Target_Station  Distance  Diff_Time  \
0       0     0               1               2  0.621531        341   
1       1     0               2               3  0.583005         45   
2       2     0               3               4  0.533489         64   
3       3     0               4               5  0.560464        113   
4       4     0               5               6  1.137853        154   
5       5     0               6               7  0.470693         62   
6       6     0               7               8  0.363559         33   
7       7     0               8               9  0.657603         74   
8       8     0               9              10  0.211337         90   
9       9     0              10              11  0.516312        133   
10     10     0              11              12  0.475580         90   
11     11     0              12              13  0.300321         40   
12     12     0              13              14  0.464933         52   
13     13     0              14              15  1.335214        185   
14     14     0              15              16  0.586234        121   
15     15     0              16              17  0.216303         39   
16     16     0              17              18  0.406526         70   
17     17     0              18              19  0.556968        151   
18     18     0              19              20  1.037118        130   
19     19     0              20              21  0.184317         39   
20     20     0              21              22  0.455232         44   
21     21     0              22              23  0.619070         94   
22     22     0              23              24  0.600119        121   
23     23     0              24              25  0.476415         29   
24     24     0              25              26  0.332997         36   
25     25     0              26              27  0.468843         71   
26     27     0              28              29  0.286119         21   
27     28     0              29              30  0.322967         71   
28     29     1               3               4  0.997548        480   
29     30     1               4               5  0.634857        110   
..    ...   ...             ...             ...       ...        ...   
42     56     0               5               6  0.515931         80   
43     57     0               6               7  0.757535         80   
44     58     0               7               8  1.022667        120   
45     59     1               1               2  0.597859        120   
46     11     0               6               7  0.750089         90   
47     12     0               7               8  1.013736        130   
48     13     1               1               2  0.619243        790   
49     14     1               2               3  0.947343        100   
50     15     1               3               4  0.756596         90   
51     16     1               4               5  0.444499         70   
52     17     1               5               6  0.856311        190   
53     18     1               6               7  1.281640        220   
54     19     1               7               8  0.474778         90   
55     20     0               3               4  2.385840        780   
56     21     0               4               5  0.598337        130   
57     22     0               5               6  0.531152        120   
58     23     0               6               7  0.708724         80   
59     24     0               7               8  1.062552        120   
60     25     1               1               2  0.530822        730   
61     26     1               2               3  1.018405        140   
62     27     1               3               4  0.794306         90   
63     28     1               4               5  0.441209        121   
64     29     1               5               6  0.755656        300   
65     30     1               6             

In [10]:
with open('./data/train-id4-crowd-grid2.txt', 'rb') as data_file:
    train = pickle.load(data_file)
# with open('./data/test-id-crowd-grid.txt', 'wb') as data_file:
#     pickle.dump(test_5, data_file)

In [205]:
del hi['Source_loc']
del hi['end_loc']
with open('./data/train-id-crowd-grid2.txt', 'wb') as data_file:
    pickle.dump(hi, data_file)

/home/b418-xiwei/anaconda3/envs/dl/lib/python3.6/site-packages/tqdm/_monitor.py:89: TqdmSynchronisationWarning: Set changed size during iteration (see https://github.com/tqdm/tqdm/issues/481)
  TqdmSynchronisationWarning)


In [206]:
hi.columns

Index(['Unnamed: 0', 'ID', 'O_LINENO', 'O_UP', 'Source_Station',
       'Target_Station', 'Distance', 'O_TIME', 'aver_v', 'hour', 'is_peek',
       'weekday', 'is_workday', 'dws', 'nws', 'dts', 'nts', 'is_rain', 'max_v',
       'h_aver_diff', 'h_aver_d', 'h_aver_v', 'Diff_Time', 's_x', 's_y', 'e_x',
       'e_y', 'is_crowd', 's_ij', 'e_ij'],
      dtype='object')

/home/b418-xiwei/anaconda3/envs/dl/lib/python3.6/site-packages/tqdm/_monitor.py:89: TqdmSynchronisationWarning: Set changed size during iteration (see https://github.com/tqdm/tqdm/issues/481)
  TqdmSynchronisationWarning)


In [7]:
# def find_history_dist(num,is_rain,is_workday,is_peek,on,start_station,next_station,time):
#     with open('./history/'+str(num)+'_'+str(is_rain)+'_'+str(is_workday)+'_'+str(is_peek)+'.txt', 'rb') as data_file:
#         b = pickle.load(data_file).reset_index()
#         b = b[(b['O_TIME']<time)]
#         b = b.groupby(['O_UP','Source_Station','Target_Station']).mean().reset_index()
#         # 	O_UP 	Source_Station 	Target_Station
#         b = b[(b['O_UP']==on)&(b['Source_Station']==start_station)&(b['Target_Station']==next_station)]
#         if b.shape[0] > 0:
#             return b.iloc[0]
#         else :
#             dic = {'Distance':[-1],'Diff_Time':[-1]}
#             x = pd.DataFrame(dic)
#             return x.iloc[0]
hi

index  O_UP  Source_Station  Target_Station  Distance  Diff_Time  \
0       0     0               1               2  0.621531        341   
1       1     0               2               3  0.583005         45   
2       2     0               3               4  0.533489         64   
3       3     0               4               5  0.560464        113   
4       4     0               5               6  1.137853        154   
5       5     0               6               7  0.470693         62   
6       6     0               7               8  0.363559         33   
7       7     0               8               9  0.657603         74   
8       8     0               9              10  0.211337         90   
9       9     0              10              11  0.516312        133   
10     10     0              11              12  0.475580         90   
11     11     0              12              13  0.300321         40   
12     12     0              13              14  0.464933         52   
13     13     0              14              15  1.335214        185   
14     14     0              15              16  0.586234        121   
15     15     0              16              17  0.216303         39   
16     16     0              17              18  0.406526         70   
17     17     0              18              19  0.556968        151   
18     18     0              19              20  1.037118        130   
19     19     0              20              21  0.184317         39   
20     20     0              21              22  0.455232         44   
21     21     0              22              23  0.619070         94   
22     22     0              23              24  0.600119        121   
23     23     0              24              25  0.476415         29   
24     24     0              25              26  0.332997         36   
25     25     0              26              27  0.468843         71   
26     27     0              28              29  0.286119         21   
27     28     0              29              30  0.322967         71   
28     29     1               3               4  0.997548        480   
29     30     1               4               5  0.634857        110   
..    ...   ...             ...             ...       ...        ...   
42     56     0               5               6  0.515931         80   
43     57     0               6               7  0.757535         80   
44     58     0               7               8  1.022667        120   
45     59     1               1               2  0.597859        120   
46     11     0               6               7  0.750089         90   
47     12     0               7               8  1.013736        130   
48     13     1               1               2  0.619243        790   
49     14     1               2               3  0.947343        100   
50     15     1               3               4  0.756596         90   
51     16     1               4               5  0.444499         70   
52     17     1               5               6  0.856311        190   
53     18     1               6               7  1.281640        220   
54     19     1               7               8  0.474778         90   
55     20     0               3               4  2.385840        780   
56     21     0               4               5  0.598337        130   
57     22     0               5               6  0.531152        120   
58     23     0               6               7  0.708724         80   
59     24     0               7               8  1.062552        120   
60     25     1               1               2  0.530822        730   
61     26     1               2               3  1.018405        140   
62     27     1               3               4  0.794306         90   
63     28     1               4               5  0.441209        121   
64     29     1               5               6  0.755656        300   
65     30     1               6             

In [4]:
with open('./data/full_history_plus', 'rb') as data_file:
    hi = pickle.load(data_file)
hi['Line'].drop_duplicates().shape

(428,)

In [10]:
hi

index  O_UP  Source_Station  Target_Station  Distance  Diff_Time  \
0       0     0               1               2  0.621531        341   
1       1     0               2               3  0.583005         45   
2       2     0               3               4  0.533489         64   
3       3     0               4               5  0.560464        113   
4       4     0               5               6  1.137853        154   
5       5     0               6               7  0.470693         62   
6       6     0               7               8  0.363559         33   
7       7     0               8               9  0.657603         74   
8       8     0               9              10  0.211337         90   
9       9     0              10              11  0.516312        133   
10     10     0              11              12  0.475580         90   
11     11     0              12              13  0.300321         40   
12     12     0              13              14  0.464933         52   
13     13     0              14              15  1.335214        185   
14     14     0              15              16  0.586234        121   
15     15     0              16              17  0.216303         39   
16     16     0              17              18  0.406526         70   
17     17     0              18              19  0.556968        151   
18     18     0              19              20  1.037118        130   
19     19     0              20              21  0.184317         39   
20     20     0              21              22  0.455232         44   
21     21     0              22              23  0.619070         94   
22     22     0              23              24  0.600119        121   
23     23     0              24              25  0.476415         29   
24     24     0              25              26  0.332997         36   
25     25     0              26              27  0.468843         71   
26     27     0              28              29  0.286119         21   
27     28     0              29              30  0.322967         71   
28     29     1               3               4  0.997548        480   
29     30     1               4               5  0.634857        110   
..    ...   ...             ...             ...       ...        ...   
42     56     0               5               6  0.515931         80   
43     57     0               6               7  0.757535         80   
44     58     0               7               8  1.022667        120   
45     59     1               1               2  0.597859        120   
46     11     0               6               7  0.750089         90   
47     12     0               7               8  1.013736        130   
48     13     1               1               2  0.619243        790   
49     14     1               2               3  0.947343        100   
50     15     1               3               4  0.756596         90   
51     16     1               4               5  0.444499         70   
52     17     1               5               6  0.856311        190   
53     18     1               6               7  1.281640        220   
54     19     1               7               8  0.474778         90   
55     20     0               3               4  2.385840        780   
56     21     0               4               5  0.598337        130   
57     22     0               5               6  0.531152        120   
58     23     0               6               7  0.708724         80   
59     24     0               7               8  1.062552        120   
60     25     1               1               2  0.530822        730   
61     26     1               2               3  1.018405        140   
62     27     1               3               4  0.794306         90   
63     28     1               4               5  0.441209        121   
64     29     1               5               6  0.755656        300   
65     30     1               6             

In [3]:
with open('station_map.pkl','rb') as f:
    station_map = pickle.load(f)

In [24]:
i=0
print(hi.iloc[i])
station_map[(int(hi.iloc[i]['Line']),hi.iloc[i]['O_UP'],hi.iloc[i]['Source_Station'])]

index                               0
O_UP                                0
Source_Station                      1
Target_Station                      2
Distance                     0.621531
Diff_Time                         341
O_TIME            2017-10-15 06:05:42
Line                                1
is_rain                             0
is_workday                          0
is_peek                             0
s_x                           39.1277
s_y                           117.197
e_x                           39.1258
e_y                           117.199
s_ij                              569
e_ij                              569
Name: 0, dtype: object


2206

In [ ]:
from tqdm import tqdm, tqdm_pandas
tqdm.pandas()

hi['source_id'] = hi.progress_apply(lambda x : station_map[(int(x['Line']),x['O_UP'],x['Source_Station'])],axis=1)
hi['target_id'] = hi.progress_apply(lambda x : station_map[(int(x['Line']),x['O_UP'],x['Target_Station'])],axis=1)

In [5]:
from tqdm import tqdm, tqdm_pandas
def ret_map(a,b,c):
    if (int(a),b,c) in station_map:
        return station_map[(int(a),b,c)]
    else:
        return -1
tqdm.pandas()
hi['source_id'] = hi.progress_apply(lambda x : ret_map(x['Line'],x['O_UP'],x['Source_Station']) ,axis=1)
hi['target_id'] = hi.progress_apply(lambda x : ret_map(x['Line'],x['O_UP'],x['Target_Station']),axis=1)
hi

100%|██████████| 17301720/17301720 [24:47<00:00, 11631.00it/s]


index  O_UP  Source_Station  Target_Station  Distance  Diff_Time  \
0       0     0               1               2  0.621531        341   
1       1     0               2               3  0.583005         45   
2       2     0               3               4  0.533489         64   
3       3     0               4               5  0.560464        113   
4       4     0               5               6  1.137853        154   
5       5     0               6               7  0.470693         62   
6       6     0               7               8  0.363559         33   
7       7     0               8               9  0.657603         74   
8       8     0               9              10  0.211337         90   
9       9     0              10              11  0.516312        133   
10     10     0              11              12  0.475580         90   
11     11     0              12              13  0.300321         40   
12     12     0              13              14  0.464933         52   
13     13     0              14              15  1.335214        185   
14     14     0              15              16  0.586234        121   
15     15     0              16              17  0.216303         39   
16     16     0              17              18  0.406526         70   
17     17     0              18              19  0.556968        151   
18     18     0              19              20  1.037118        130   
19     19     0              20              21  0.184317         39   
20     20     0              21              22  0.455232         44   
21     21     0              22              23  0.619070         94   
22     22     0              23              24  0.600119        121   
23     23     0              24              25  0.476415         29   
24     24     0              25              26  0.332997         36   
25     25     0              26              27  0.468843         71   
26     27     0              28              29  0.286119         21   
27     28     0              29              30  0.322967         71   
28     29     1               3               4  0.997548        480   
29     30     1               4               5  0.634857        110   
..    ...   ...             ...             ...       ...        ...   
42     56     0               5               6  0.515931         80   
43     57     0               6               7  0.757535         80   
44     58     0               7               8  1.022667        120   
45     59     1               1               2  0.597859        120   
46     11     0               6               7  0.750089         90   
47     12     0               7               8  1.013736        130   
48     13     1               1               2  0.619243        790   
49     14     1               2               3  0.947343        100   
50     15     1               3               4  0.756596         90   
51     16     1               4               5  0.444499         70   
52     17     1               5               6  0.856311        190   
53     18     1               6               7  1.281640        220   
54     19     1               7               8  0.474778         90   
55     20     0               3               4  2.385840        780   
56     21     0               4               5  0.598337        130   
57     22     0               5               6  0.531152        120   
58     23     0               6               7  0.708724         80   
59     24     0               7               8  1.062552        120   
60     25     1               1               2  0.530822        730   
61     26     1               2               3  1.018405        140   
62     27     1               3               4  0.794306         90   
63     28     1               4               5  0.441209        121   
64     29     1               5               6  0.755656        300   
65     30     1               6             

In [6]:
with open('./data/full_history2', 'wb') as data_file:
    pickle.dump(hi, data_file)
print('finished')

finished


In [28]:
hi.groupby(['Line', 'O_UP','source_id','target_id']).apply(lambda x:x.sort_values(by='O_TIME', ascending=True))

index  O_UP  Source_Station  \
Line O_UP source_id target_id                                      
1    0    -1        2122      2          2     0               3   
                              245     5537     0               3   
                              58       579     0               3   
                              207     2198     0               3   
                              154     1513     0               3   
                              415     4437     0               3   
                              460     4905     0               3   
                              296     2935     0               3   
                              106     1056     0               3   
                              353     3808     0               3   
                              138     1245     0               3   
                              196     1690     0               3   
                              506     5170     0               3   
                              319     3244     0               3   
                              417      337     0               3   
                              594      634     0               3   
                              1650    3573     0               3   
                              1159    2475     0               3   
                              960     1568     0               3   
                              1111    2253     0               3   
                              2104    4492     0               3   
                              777     1111     0               3   
                              1927    4117     0               3   
                              2030    4317     0               3   
                              2382    4960     0               3   
                              293       99     0               3   
                              1586    3299     0               3   
                              2249    4721     0               3   
                              471      392     0               3   
                              645      689     0               3   
...                                    ...   ...             ...   
97   1     3061     1939      7634      74     1              13   
                              7716     835     1              13   
                              7662     192     1              13   
                              15957    943     1              13   
                              15867    770     1              13   
                              15604    172     1              13   
                              15733    496     1              13   
                              15649    288     1              13   
                              15556     96     1              13   
                              15685    394     1              13   
                              15518     38     1              13   
                              15979    966     1              13   
                              15884    790     1              13   
                              15754    518     1              13   
                              16044   1050     1              13   
                              15833    683     1              13   
                              15535     56     1              13   
                              15706    416     1              13   
                              15908    816     1              13   
                              15773    539     1              13   
                              15587    129     1              13   
                              15794    596     1              13   
                              7865    1080     1              13   
                              7861     894     1              13   
                              16072    243     1              13   
                              16188    734     1              13   
                         

In [ ]:
# data['hour'] = data['O_TIME'].apply(lambda x: x.hour)
# data['weekday'] =  busmaxv.iloc[0]['O_TIME'].weekday()
# weat = weather[(weather['days'] == '2017-10-' + day)].iloc[0]
# data['dws'] = weat['dws_onehot']
# data['nws'] = weat['nws_onehot']
# data['dts'] = weat['dts']
# data['nts'] = weat['nts']

In [29]:
hi = hi.groupby(['Line', 'O_UP','source_id','target_id','is_rain','is_workday','is_peek']).mean().reset_index()
hi

Line  O_UP  source_id  target_id is_rain is_workday is_peek  \
0         1     0         -1       2122       0          0       0   
1         1     0         -1       2122       0          0       1   
2         1     0         -1       2122       0          1       0   
3         1     0         -1       2122       0          1       1   
4         1     0         -1       2122       1          0       0   
5         1     0         -1       2122       1          0       1   
6         1     0         -1       2122       1          1       0   
7         1     0         -1       2122       1          1       1   
8         1     0         -1       2772       0          0       0   
9         1     0         -1       2772       0          0       1   
10        1     0         -1       2772       0          1       0   
11        1     0         -1       2772       0          1       1   
12        1     0         -1       2772       1          0       0   
13        1     0         -1       2772       1          0       1   
14        1     0         -1       2772       1          1       0   
15        1     0         -1       2772       1          1       1   
16        1     0         16       1393       0          0       0   
17        1     0         16       1393       0          0       1   
18        1     0         16       1393       0          1       0   
19        1     0         16       1393       0          1       1   
20        1     0         16       1393       1          0       0   
21        1     0         16       1393       1          0       1   
22        1     0         16       1393       1          1       0   
23        1     0         16       1393       1          1       1   
24        1     0         17        625       0          0       0   
25        1     0         17        625       0          0       1   
26        1     0         17        625       0          1       0   
27        1     0         17        625       0          1       1   
28        1     0         17        625       1          0       0   
29        1     0         17        625       1          0       1   
...     ...   ...        ...        ...     ...        ...     ...   
161854   97     1       2309       1937       0          1       0   
161855   97     1       2309       1937       0          1       1   
161856   97     1       2309       1937       1          0       0   
161857   97     1       2309       1937       1          0       1   
161858   97     1       2309       1937       1          1       0   
161859   97     1       2309       1937       1          1       1   
161860   97     1       2439         -1       0          0       0   
161861   97     1       2439         -1       0          0       1   
161862   97     1       2439         -1       0          1       0   
161863   97     1       2439         -1       0          1       1   
161864   97     1       2439         -1       1          0       0   
161865   97     1       2439         -1       1          0       1   
161866   97     1       2439         -1       1          1       0   
161867   97     1       2439         -1       1          1       1   
161868   97     1       2742       1274       0          0       0   
161869   97     1       2742       1274       0          0       1   
161870   97     1       2742       1274       0          1       0   
161871   97     1       2742       1274       0          1       1   
161872   97     1       2742       1274       1          0       0   
161873   97     1       2742       1274       1          0       1   
161874   97     1       2742       1274       1          1       0   
161875   97     1       2742       1274       1          1       1   
161876   97     1       3061       1939       0          0       0   
161877   97     1       3061       1939       0          0       1   
161878   97     1       3061       1939       0          1       0   
161879   97     1

In [38]:
b = hi[(hi['Line']==1)&(hi['O_UP']==0)&(hi['source_id']==16)&(hi['target_id']==1393)&(hi['is_workday']==0)&(hi['is_peek']==0)]#
b

Line  O_UP  source_id  target_id  is_rain  is_workday  is_peek  \
16     1     0         16       1393        0           0        0   
20     1     0         16       1393        1           0        0   

          index  Source_Station  Target_Station  Distance  Diff_Time  \
16  2433.525773             7.0             8.0  0.345632  52.113402   
20  2887.165138             7.0             8.0  0.356233  52.211009   

         s_x         s_y        e_x         e_y   s_ij   e_ij  
16  39.12878  117.179398  39.129398  117.182999  569.0  569.0  
20  39.12878  117.179398  39.129398  117.182999  569.0  569.0

In [37]:
hi.dtypes

Line                int64
O_UP                int64
source_id           int64
target_id           int64
is_rain             int64
is_workday          int64
is_peek             int64
index             float64
Source_Station    float64
Target_Station    float64
Distance          float64
Diff_Time         float64
s_x               float32
s_y               float32
e_x               float32
e_y               float32
s_ij              float64
e_ij              float64
dtype: object

In [36]:
hi.shape
hi['Line'] = hi['Line'].astype('int') 
hi['is_workday'] = hi['is_workday'].astype('int') 
hi['is_peek'] = hi['is_peek'].astype('int') 
hi['is_rain'] = hi['is_rain'].astype('int') 

In [42]:
with open('./data/train-id4-crowd-grid4.txt', 'rb') as data_file:
    train = pickle.load(data_file)

In [39]:
def get_grid_history(l,o,s,t,w,p,r):
    b = hi[(hi['Line']==l)&(hi['O_UP']==o)&(hi['source_id']==s)&(hi['target_id']==t)&(hi['is_workday']==w)&(hi['is_peek']==p)&(hi['is_rain']==r)]#
    if b.shape[0] > 0:
        return b.iloc[0]
    else :
        dic = {'Distance':[-1],'Diff_Time':[-1]}
        x = pd.DataFrame(dic)
        return x.iloc[0]


In [43]:
train_10 = train[:10]
tmp = train_10.apply(lambda x : get_grid_history(x['O_LINENO'],x['O_UP'],x['Source_Station_encode'],x['Target_Station_encode'],x['is_workday'],x['is_peek'],x['is_rain']), axis=1)
train_10['encode_aver_diff'] = tmp['Diff_Time']
train_10['encode_aver_d'] = tmp['Distance']
train_10

/home/kawayi-4/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  This is separate from the ipykernel package so we can avoid doing imports until
/home/kawayi-4/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  after removing the cwd from sys.path.


Unnamed: 0        ID  O_LINENO  O_UP  Source_Station  Target_Station  \
0           1  80412021       804     1              20              21   
1           2  80412122       804     1              21              22   
2           3  80412223       804     1              22              23   
3           4  80412324       804     1              23              24   
4           5  80412425       804     1              24              25   
5           6  80400203       804     0               2               3   
6           7  80400304       804     0               3               4   
7           8  80400405       804     0               4               5   
8           9  80400506       804     0               5               6   
9          10  80400607       804     0               6               7   

   Distance               O_TIME     aver_v  hour      ...        is_crowd  \
0  0.629329  2017-10-09 06:31:28  16.182736     6      ...               0   
1  0.983431  2017-10-09 06:35:18  15.392834     6      ...               0   
2  0.690608  2017-10-09 06:36:28  35.516963     6      ...               1   
3  0.608654  2017-10-09 06:37:38  31.302190     6      ...               1   
4  0.362356  2017-10-09 06:38:28  26.089661     6      ...               0   
5  3.064650  2017-10-09 06:58:15   9.294643     6      ...               0   
6  0.846219  2017-10-09 07:00:04  27.948529     7      ...               0   
7  0.556623  2017-10-09 07:04:04   8.349346     7      ...               0   
8  0.582659  2017-10-09 07:05:54  19.068836     7      ...               0   
9  1.290634  2017-10-09 07:09:34  21.119466     7      ...               0   

   s_ij  e_ij          ID2  grid_aver_diff  grid_aver_d  \
0   569   569  80405690569      215.775253     0.723450   
1   569   569  80405690569      241.289308     0.949461   
2   569   569  80405690569      124.409653     0.644947   
3   569   569  80405690569      162.265997     0.580119   
4   569   569  80405690569       84.416979     0.488454   
5   569   569  80405690569      376.263986     1.426270   
6   569   569  80405690569      186.824074     0.870210   
7   569   569  80405690569      179.120181     0.595381   
8   569   569  80405690569      103.030108     0.559572   
9   569   603  80405690603      338.263393     1.358558   

   Source_Station_encode  Target_Station_encode  encode_aver_diff  \
0                   3500                     66        212.965000   
1                     66                     61        242.592965   
2                     61                    208        127.215686   
3                    208                   2466        161.722772   
4                   2466                     33         84.300493   
5                     67                     61        360.953020   
6                     61                   4566        177.596491   
7                   4566                   1006        179.400000   
8                   1006                   2178        102.221311   
9                   2178                   3844        353.857143   

   encode_aver_d  
0       0.731085  
1       0.947346  
2       0.660748  
3       0.579162  
4       0.491358  
5       1.424962  
6       0.865024  
7       0.584043  
8       0.567292  
9       1.379284  

[10 rows x 37 columns]

In [53]:
cols=['Unnamed: 0', 'ID', 'O_LINENO', 'O_UP', 'Source_Station',
       'Target_Station', 'Distance', 'O_TIME', 'aver_v', 'hour', 'is_peek',
       'weekday', 'is_workday', 'dws', 'nws', 'dts', 'nts', 'is_rain', 'max_v','Diff_Time', 's_x', 's_y', 'e_x',
       'e_y', 'is_crowd', 's_ij', 'e_ij', 'ID2',
       'h_aver_diff', 'h_aver_d', 'h_aver_v',  'grid_aver_diff',
       'grid_aver_d']
train_10=train_10.ix[:,cols]
train_10

/home/b418-xiwei/anaconda3/envs/dl/lib/python3.6/site-packages/ipykernel_launcher.py:7: DeprecationWarning: 
.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/indexing.html#ix-indexer-is-deprecated
  import sys


Unnamed: 0        ID  O_LINENO  O_UP  Source_Station  Target_Station  \
0           1  80412021       804     1              20              21   
1           2  80412122       804     1              21              22   
2           3  80412223       804     1              22              23   
3           4  80412324       804     1              23              24   
4           5  80412425       804     1              24              25   
5           6  80400203       804     0               2               3   
6           7  80400304       804     0               3               4   
7           8  80400405       804     0               4               5   
8           9  80400506       804     0               5               6   
9          10  80400607       804     0               6               7   

   Distance               O_TIME     aver_v  hour     ...            e_y  \
0  0.629329  2017-10-09 06:31:28  16.182736     6     ...       117.1904   
1  0.983431  2017-10-09 06:35:18  15.392834     6     ...       117.1840   
2  0.690608  2017-10-09 06:36:28  35.516963     6     ...       117.1800   
3  0.608654  2017-10-09 06:37:38  31.302190     6     ...       117.1810   
4  0.362356  2017-10-09 06:38:28  26.089661     6     ...       117.1840   
5  3.064650  2017-10-09 06:58:15   9.294643     6     ...       117.1840   
6  0.846219  2017-10-09 07:00:04  27.948529     7     ...       117.1898   
7  0.556623  2017-10-09 07:04:04   8.349346     7     ...       117.1964   
8  0.582659  2017-10-09 07:05:54  19.068836     7     ...       117.2022   
9  1.290634  2017-10-09 07:09:34  21.119466     7     ...       117.2134   

   is_crowd  s_ij  e_ij          ID2  h_aver_diff  h_aver_d   h_aver_v  \
0         0   569   569  80405690569   212.965000  0.731085  12.358399   
1         0   569   569  80405690569   242.592965  0.947346  14.058298   
2         1   569   569  80405690569   127.215686  0.660748  18.698118   
3         1   569   569  80405690569   161.722772  0.579162  12.892321   
4         0   569   569  80405690569    84.300493  0.491358  20.983152   
5         0   569   569  80405690569   360.953020  1.424962  14.212002   
6         0   569   569  80405690569   177.596491  0.865024  17.534618   
7         0   569   569  80405690569   179.400000  0.584043  11.719934   
8         0   569   569  80405690569   102.221311  0.567292  19.978714   
9         0   569   603  80405690603   353.857143  1.379284  14.032283   

   grid_aver_diff  grid_aver_d  
0      215.775253     0.723450  
1      241.289308     0.949461  
2      124.409653     0.644947  
3      162.265997     0.580119  
4       84.416979     0.488454  
5      376.263986     1.426270  
6      186.824074     0.870210  
7      179.120181     0.595381  
8      103.030108     0.559572  
9      338.263393     1.358558  

[10 rows x 33 columns]

In [44]:
tmp = train.progress_apply(lambda x : get_grid_history(x['O_LINENO'],x['O_UP'],x['Source_Station_encode'],x['Target_Station_encode'],x['is_workday'],x['is_peek'],x['is_rain']), axis=1)
train['encode_aver_diff'] = tmp['Diff_Time']
train['encode_aver_d'] = tmp['Distance']
train


  0%|          | 3481/13963746 [01:20<22:29:40, 172.39it/s]


KeyboardInterrupt: 


  0%|          | 3501/13963746 [01:33<21:52:16, 177.30it/s]

In [55]:
with open('./data/train-id4-crowd-grid3.txt', 'wb') as data_file:
    pickle.dump(train, data_file)

In [11]:
with open('./data/train-id4-crowd-grid3.txt', 'rb') as data_file:
    train = pickle.load(data_file)
train

Unnamed: 0          ID  O_LINENO  O_UP  Source_Station  \
0                  1    80412021       804     1              20   
1                  2    80412122       804     1              21   
2                  3    80412223       804     1              22   
3                  4    80412324       804     1              23   
4                  5    80412425       804     1              24   
5                  6    80400203       804     0               2   
6                  7    80400304       804     0               3   
7                  8    80400405       804     0               4   
8                  9    80400506       804     0               5   
9                 10    80400607       804     0               6   
10                11    80400708       804     0               7   
11                12    80400809       804     0               8   
12                13    80400910       804     0               9   
13                14    80401011       804     0              10   
14                15    80401112       804     0              11   
15                16    80401213       804     0              12   
16                17    80401314       804     0              13   
17                18    80401415       804     0              14   
18                19    80401516       804     0              15   
19                20    80401617       804     0              16   
20                21    80401718       804     0              17   
21                22    80401819       804     0              18   
22                23    80401920       804     0              19   
23                24    80402021       804     0              20   
24                25    80402122       804     0              21   
25                26    80402223       804     0              22   
26                28    80410203       804     1               2   
27                29    80410304       804     1               3   
28                30    80410405       804     1               4   
29                31    80410506       804     1               5   
...              ...         ...       ...   ...             ...   
13963716          10  5501200304     55012     0               3   
13963717          11  5501200405     55012     0               4   
13963718          12  5501200506     55012     0               5   
13963719          13  5501200607     55012     0               6   
13963720          14  5501200708     55012     0               7   
13963721          15  5501200809     55012     0               8   
13963722          17  5501210405     55012     1               4   
13963723          18  5501210506     55012     1               5   
13963724          19  5501210607     55012     1               6   
13963725          20  5501210708     55012     1               7   
13963726          21  5501210809     55012     1               8   
13963727          23  5501200203     55012     0               2   
13963728          24  5501200304     55012     0               3   
13963729          25  5501200405     55012     0               4   
13963730          26  5501200506     55012     0               5   
13963731          27  5501200607     55012     0               6   
13963732          28  5501200708     55012     0               7   
13963733          29  5501200809     55012     0               8   
13963734           1  5500910203     55009     1               2   
13963735           2  5500910304     55009     1               3   
13963736           3  5500910405     55009     1               4   
13963737           4  5500910506     55009     1               5   
13963738           6  5500900203     55009     0               2   
13963739           7  5500900304     55009     0               3   
13963740           8  5500900405     55009     0               4   
13963741           9  5500900506     55009     0               5   
13963742          11  5500910203     55009     1               2  

In [15]:
bus = train[(train['O_LINENO']==1)&(train['O_UP']==0)&(train['O_TIME']>'2017-10-10 09:00:00')&(train['O_TIME']<'2017-10-10 10:00:00')]
bus[['O_TIME','Source_Station','Target_Station','Diff_Time']]

O_TIME  Source_Station  Target_Station  Diff_Time
840083  2017-10-10 09:00:02              15              16        120
840084  2017-10-10 09:00:57              16              17         55
840085  2017-10-10 09:01:49              17              18         52
840086  2017-10-10 09:03:39              18              19        110
840087  2017-10-10 09:06:50              19              20        191
840088  2017-10-10 09:07:40              20              21         50
840089  2017-10-10 09:09:00              21              22         80
840090  2017-10-10 09:10:40              22              23        100
840091  2017-10-10 09:13:10              23              24        150
840092  2017-10-10 09:14:19              24              25         69
840093  2017-10-10 09:15:19              25              26         60
840094  2017-10-10 09:16:40              26              27         81
840095  2017-10-10 09:18:00              27              28         80
840096  2017-10-10 09:19:00              28              29         60
840097  2017-10-10 09:20:00              29              30         60
840291  2017-10-10 09:52:56               1               2       1450
840292  2017-10-10 09:56:36               2               3        220
840293  2017-10-10 09:56:46               3               4         10
840294  2017-10-10 09:57:46               4               5         60
840614  2017-10-10 09:49:42              29              30         42
840917  2017-10-10 09:01:44               5               6        196
840918  2017-10-10 09:03:19               6               7         95
840919  2017-10-10 09:04:29               7               8         70
840920  2017-10-10 09:05:49               8               9         80
840921  2017-10-10 09:07:23               9              10         94
840922  2017-10-10 09:09:07              10              11        104
840923  2017-10-10 09:11:07              11              12        120
840924  2017-10-10 09:12:17              12              13         70
840925  2017-10-10 09:13:17              13              14         60
840926  2017-10-10 09:17:06              14              15        229
...                     ...             ...             ...        ...
843685  2017-10-10 09:54:31              26              27        100
843686  2017-10-10 09:55:42              27              28         71
843687  2017-10-10 09:56:22              28              29         40
843688  2017-10-10 09:57:12              29              30         50
844487  2017-10-10 09:01:15               4               5        100
844488  2017-10-10 09:04:06               5               6        171
844489  2017-10-10 09:05:27               6               7         81
844490  2017-10-10 09:06:17               7               8         50
844491  2017-10-10 09:08:17               8               9        120
844492  2017-10-10 09:08:53               9              10         36
844493  2017-10-10 09:11:13              10              11        140
844494  2017-10-10 09:13:53              11              12        160
844495  2017-10-10 09:15:03              12              13         70
844496  2017-10-10 09:16:33              13              14         90
844497  2017-10-10 09:19:47              14              15        194
844498  2017-10-10 09:25:07              15              16        320
844499  2017-10-10 09:25:57              16              17         50
844500  2017-10-10 09:27:07              17              18         70
844501  2017-10-10 09:28:37              18              19         90
844502  2017-10-10 09:31:29              19              20        172
844503  2017-10-10 09:32:09              20              21         40
844504  2017-10-10 09:33:09              21              22         60
844505  2017-10-10 09:34:59              22              23        110
844506  2017-10-10 09:37:19              23              24        140
844507  2017-10-10 09:37:57              24  

In [ ]:
tmp1 = test.progress_apply(lambda x : get_grid_history(x['O_LINENO'],x['O_UP'],x['Source_Station'],x['Target_Station'],x['is_workday'],x['is_peek'],x['s_ij'],x['e_ij']), axis=1)
test['grid_aver_diff'] = tmp1['Diff_Time']
test['grid_aver_d'] = tmp1['Distance']
test

  0%|          | 1239/490380 [00:09<52:27, 155.43it/s] /home/b418-xiwei/anaconda3/envs/dl/lib/python3.6/site-packages/tqdm/_monitor.py:89: TqdmSynchronisationWarning: Set changed size during iteration (see https://github.com/tqdm/tqdm/issues/481)
  TqdmSynchronisationWarning)
100%|██████████| 490380/490380 [59:50<00:00, 133.47it/s]  

In [ ]:
with open('./data/test-id4-crowd-grid3.txt', 'wb') as data_file:
    pickle.dump(test, data_file)